<a href="https://colab.research.google.com/github/tthandi/magic_formula_project/blob/main/alphaVantageDataLoader.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Test for adjusted price data for popular and delisted tickers

In [ ]:
#!/usr/bin/env python3
"""
av_history_depth_plus.py  (revised – no CIK assumption)
"""

import os, io, csv, json, time, requests, pandas as pd
from datetime import date

API_KEY = os.getenv("AV_API_KEY")
if not API_KEY:
    raise SystemExit("export AV_API_KEY first")

BASE  = "https://www.alphavantage.co/query"
SLEEP = 0.8    # throttle ~75 req/min

# ── ticker universe (active + delisted sample) ─────────────────────────
LONG_LIVED = {
    "IBM": "International Business Machines",
    "GE":  "General Electric",
    "KO":  "Coca-Cola Company",
    "PG":  "Procter & Gamble",
}
DELISTED = {
    "USG":   "USG Corp – private 2019",
    "DWA":   "DreamWorks – bought 2016",
    "SKUL":  "Skullcandy – private 2016",
    "SYX":   "Systemax – ticker now GIC",
    "KRFT":  "Kraft Foods Group – merged 2015",
    "LEHMQ": "Lehman Brothers – bankruptcy 2008",
    "ENRNQ": "Enron – bankruptcy 2001",
}
TICKERS = {**LONG_LIVED, **DELISTED}

ENDPOINTS = {
    "DAILY":   {"function": "TIME_SERIES_DAILY_ADJUSTED",   "outputsize": "full"},
    "WEEKLY":  {"function": "TIME_SERIES_WEEKLY_ADJUSTED"},
    "MONTHLY": {"function": "TIME_SERIES_MONTHLY_ADJUSTED"},
}

# ── download listing snapshots once ────────────────────────────────────
def fetch_listing(state: str) -> pd.DataFrame:
    r = requests.get(BASE, params={
        "function": "LISTING_STATUS",
        "state": state,
        "datatype": "csv",
        "apikey": API_KEY}, timeout=20)
    r.raise_for_status()
    df = pd.read_csv(io.StringIO(r.text))
    df.columns = [c.lower() for c in df.columns]      # normalise
    return df

print("Downloading LISTING_STATUS snapshots …")
active_df   = fetch_listing("active")
delisted_df = fetch_listing("delisted")
active_set   = set(active_df["symbol"])
delisted_set = set(delisted_df["symbol"])

# (optional) build successor map here if you have manual aliases
SUCCESSOR_MAP = {
    # "SYX": "GIC",   # example
}

# ── simple resolver (no CIK fallback) ───────────────────────────────────
def resolve_symbol(sym: str) -> str:
    sym_clean = sym.rstrip("QPK")           # drop OTC suffixes
    return SUCCESSOR_MAP.get(sym_clean, sym_clean)

# ── fetch one series helper ─────────────────────────────────────────────
def fetch_series(sym: str, params: dict) -> tuple[pd.DataFrame, str]:
    r = requests.get(BASE, params=params | {"symbol": sym, "apikey": API_KEY})
    if r.status_code != 200:
        return pd.DataFrame(), f"http {r.status_code}"
    try:
        j = r.json()
    except json.JSONDecodeError:
        return pd.DataFrame(), "non-json"
    if "Note" in j:           return pd.DataFrame(), "rate-limit"
    if "Error Message" in j:  return pd.DataFrame(), "api-error"
    key = next((k for k in j if "Series" in k), None)
    if not (key and j[key]):  return pd.DataFrame(), "empty"
    df = (pd.DataFrame.from_dict(j[key], orient="index")
            .reset_index().rename(columns={"index":"date"}))
    return df, "ok"

# ── main probe loop ─────────────────────────────────────────────────────
records = []
for orig, note in TICKERS.items():
    sym = resolve_symbol(orig)
    rec = {"symbol": orig, "resolved": sym, "note": note,
           "in_active": sym in active_set, "in_delisted": sym in delisted_set}
    earliest = latest = rows = None

    for tag, ep in ENDPOINTS.items():
        df, reason = fetch_series(sym, ep)
        time.sleep(SLEEP)
        rec[f"{tag.lower()}_status"] = "✅" if not df.empty else f"❌ ({reason})"

        if earliest is None and not df.empty:          # first successful series
            earliest = df["date"].min()
            latest   = df["date"].max()
            rows     = len(df)
            df.to_csv(f"{orig}_{tag.lower()}_alpha.csv", index=False)

    rec.update({"earliest": earliest or "n/a",
                "latest"  : latest   or "n/a",
                "rows"    : rows     or 0})
    records.append(rec)

# ── summary table ───────────────────────────────────────────────────────
cols = ["symbol","resolved","note","earliest","latest","rows",
        "daily_status","weekly_status","monthly_status","in_delisted","in_active"]
df_out = pd.DataFrame(records)[cols]

print(f"\nAlpha Vantage history depth — {date.today()}\n")
print(df_out.to_markdown(index=False))


Test of daily adjusted price data for popular tickers


In [ ]:
# ----------------------------------------------------------------------
# 0. Install libraries, import modules, authenticate to GCP
# ----------------------------------------------------------------------
!pip install --quiet --upgrade pandas google-cloud-storage google-cloud-bigquery

import io, json, requests, pandas as pd
from google.colab import auth
from google.cloud import storage, bigquery
from google.cloud.exceptions import NotFound

auth.authenticate_user()

# ----------------------------------------------------------------------
# 1. Configuration
# ----------------------------------------------------------------------
PROJECT_ID  = "fluid-terminal-465516-s7"
DATASET_ID  = "spinoff_analysis"
BUCKET_NAME = "spinoff-data-main"       # ← fixed bucket; will be reused
LOCATION    = "US"
API_KEY     = "VGQMUTA2Q9WB1PDJ"
TICKERS     = ["AAPL", "MSFT", "IBM", "GE"]
YEARS       = ["2024", "2014", "2004", "1994", "1984"]

# ----------------------------------------------------------------------
# 2. Get or create GCS bucket and BigQuery dataset
# ----------------------------------------------------------------------
storage_client = storage.Client(project=PROJECT_ID)

try:
    bucket = storage_client.get_bucket(BUCKET_NAME)
    print("✅ Reusing bucket:", BUCKET_NAME)
except NotFound:
    bucket = storage_client.bucket(BUCKET_NAME)
    bucket.storage_class = "STANDARD"
    storage_client.create_bucket(bucket, location=LOCATION)
    print("✅ Created bucket:", BUCKET_NAME)

bq_client = bigquery.Client(project=PROJECT_ID)
try:
    bq_client.get_dataset(DATASET_ID)
    print("✅ BigQuery dataset exists:", DATASET_ID)
except NotFound:
    ds = bigquery.Dataset(f"{PROJECT_ID}.{DATASET_ID}")
    ds.location = LOCATION
    bq_client.create_dataset(ds)
    print("✅ Created dataset:", DATASET_ID)

# ----------------------------------------------------------------------
# 3. Helper functions
# ----------------------------------------------------------------------
def clean_cols(df: pd.DataFrame) -> pd.DataFrame:
    return df.rename(columns=lambda c: str(c).lower()
                                   .strip().replace(" ", "_").replace(".", ""))

def write_gcs(df: pd.DataFrame, blob_name: str) -> None:
    path = f"/tmp/{blob_name}"
    df.to_csv(path, index=False, encoding="utf-8")
    bucket.blob(blob_name).upload_from_filename(path)
    print("📤", f"gs://{BUCKET_NAME}/{blob_name}")

def load_bq(clean_blob: str) -> None:
    table_id = f"{PROJECT_ID}.{DATASET_ID}.{clean_blob[:-4].lower()}"
    cfg = bigquery.LoadJobConfig(
        autodetect=True,
        skip_leading_rows=1,
        source_format=bigquery.SourceFormat.CSV,
        write_disposition=bigquery.job.WriteDisposition.WRITE_TRUNCATE
    )
    uri = f"gs://{BUCKET_NAME}/{clean_blob}"
    bq_client.load_table_from_uri(uri, table_id, job_config=cfg).result()
    print("✅ BigQuery:", table_id)

def fetch_listing_status(state="active") -> pd.DataFrame:
    r = requests.get(
        "https://www.alphavantage.co/query",
        params={
            "function": "LISTING_STATUS",
            "apikey"  : API_KEY,
            "state"   : state,
            "datatype": "csv"
        },
        timeout=15
    )
    print("🔎", r.url, "→", r.status_code, len(r.text), "bytes")
    r.raise_for_status()
    return pd.read_csv(io.StringIO(r.text)) if r.text.strip() else pd.DataFrame()

def fetch_json(fn, symbol=None, **extra) -> dict:
    base = {"function": fn, "apikey": API_KEY, **extra}
    if symbol:
        base["symbol"] = symbol
    r = requests.get("https://www.alphavantage.co/query", params=base, timeout=15)
    print("🔎", r.url, "→", r.status_code)
    r.raise_for_status()
    try:
        data = r.json()
    except json.JSONDecodeError:
        print("⚠️ non-JSON response")
        return {}
    if "Note" in data:
        print("⚠️", data["Note"][:120])
    return data

# ----------------------------------------------------------------------
# 4. LISTING_STATUS (active & delisted) – run once
# ----------------------------------------------------------------------
for state in ("active", "delisted"):
    df_ls = fetch_listing_status(state)
    if not df_ls.empty:
        write_gcs(df_ls,                 f"listing_status_{state}_raw.csv")
        cleaned = clean_cols(df_ls)
        clean_name = f"listing_status_{state}.csv"
        write_gcs(cleaned, clean_name)
        load_bq(clean_name)

# ----------------------------------------------------------------------
# 5. Ticker × Year loop for daily-adjusted data
# ----------------------------------------------------------------------
for tic in TICKERS:
    print(f"\n📈 {tic} — daily-adjusted history slices")
    full_json = fetch_json("TIME_SERIES_DAILY_ADJUSTED", tic, outputsize="full")
    all_daily = full_json.get("Time Series (Daily)", {})

    for yr in YEARS:
        rows = {d: v for d, v in all_daily.items() if d.startswith(yr)}
        if not rows:
            print(f"ℹ️ {tic} has no data for {yr} — skipped")
            continue

        df = (
            pd.DataFrame.from_dict(rows, orient="index")
              .reset_index()
              .rename(columns={"index": "date"})
        )

        raw_name   = f"{tic}_daily_adjusted_{yr}_raw.csv"
        clean_name = f"{tic}_daily_adjusted_{yr}.csv"
        write_gcs(df, raw_name)
        write_gcs(clean_cols(df), clean_name)
        load_bq(clean_name)

print("\n🎉 Finished — raw CSVs in gs://{} and cleaned tables in BigQuery.".format(BUCKET_NAME))


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
alpha_vantage_market_cap_full.py  ✅  2025-11 (premium-ready)

• Computes market-cap snapshots for ALL tickers and ALL balance-sheet dates
  where Alpha Vantage reports commonStockSharesOutstanding (annual + quarterly).
• Matches each fiscal date to the most recent trading day ≤ that date using
  TIME_SERIES_DAILY_ADJUSTED (adjusted close).
• Robust:
  - API key via env var ALPHAVANTAGE_API_KEY (required)
  - Async + rate-limited (CALLS_PER_MIN=75 for premium)
  - Success-only checkpoint + failure log (Colab Drive if available)
  - Safe CSV loads (mkstemp, fixed column order), partitioned by yyyymm
  - Per-partition flush locks (avoid racey double-flush)
  - End-of-run de-dup per partition on (symbol, snapshotDate)

Modes are implicit: this script processes the AV universe minus checkpointed
symbols; re-runs will resume automatically.

Env:
  ALPHAVANTAGE_API_KEY (required)
  GOOGLE_APPLICATION_CREDENTIALS (optional, service account JSON for BigQuery)
"""

# ───────────────────────────── 1) CONFIG ─────────────────────────────
PROJECT   = "fluid-terminal-465516-s7"
DATASET   = "magic_formula"
TABLE     = "market_cap"

import os as _os
API_KEY   = 'IXNJPOSFX5OJYYQD' # REQUIRED

CALLS_PER_MIN = 75       # premium
CONCURRENCY   = 32       # parallel symbols (two AV calls each)
FLUSH_ROWS    = 5_000
AUTO_SAVE_SEC = 300

CK_DIR_NAME   = "alpha_vantage_ckpt"
CK_FILE_NAME  = "av_done_market_cap2.txt"
FAIL_FILE     = "av_failed_market_cap2.txt"

PART_START, PART_END = 198001, 204001  # yyyymm

# ───────────────────────────── 2) IMPORTS ────────────────────────────
import os as _os
import io, csv, json, time, asyncio, tempfile, aiohttp, aiolimiter, nest_asyncio, argparse, datetime as dt
from collections import defaultdict
from typing import Dict, List, Set

import pandas as pd
import requests
import tqdm
from aiolimiter import AsyncLimiter

from google.cloud import bigquery
from google.api_core import exceptions as gex
from google.auth.exceptions import DefaultCredentialsError, RefreshError
from google.oauth2 import service_account

nest_asyncio.apply()

# ───────────────── 3) BigQuery client (auth-robust) ─────────────────
def get_bq_client() -> bigquery.Client:
    # Colab user auth
    try:
        from google.colab import auth as colab_auth  # type: ignore
        colab_auth.authenticate_user()
        return bigquery.Client(project=PROJECT)
    except Exception:
        pass
    # Service account
    sa_path = _os.getenv("GOOGLE_APPLICATION_CREDENTIALS")
    if sa_path and _os.path.exists(sa_path):
        creds = service_account.Credentials.from_service_account_file(sa_path)
        return bigquery.Client(project=PROJECT, credentials=creds)
    # ADC (gcloud)
    try:
        return bigquery.Client(project=PROJECT)
    except (DefaultCredentialsError, RefreshError) as e:
        raise RuntimeError(
            "No Google Cloud credentials found. Use Colab auth, a service account via "
            "GOOGLE_APPLICATION_CREDENTIALS, or `gcloud auth application-default login`."
        ) from e

bq = get_bq_client()

# ──────────────── 4) Colab Drive checkpoint (if available) ─────────
def colab_drive_paths():
    try:
        from google.colab import drive  # type: ignore
        drive.mount("/content/drive", force_remount=False)
        root = "/content/drive/MyDrive"
        _os.makedirs(_os.path.join(root, CK_DIR_NAME), exist_ok=True)
        ck = _os.path.join(root, CK_DIR_NAME, CK_FILE_NAME)
        ff = _os.path.join(root, CK_DIR_NAME, FAIL_FILE)
        return ck, ff
    except Exception:
        return CK_FILE_NAME, FAIL_FILE

CHECKFILE, FAILFILE = colab_drive_paths()
_tqdmw = tqdm.tqdm.write
_tqdmw(f"✅ Checkpoint → {CHECKFILE}")

_ck_handle = open(CHECKFILE, "a", buffering=1)
_ck_lock   = asyncio.Lock()

async def mark_done(sym: str):
    async with _ck_lock:
        _ck_handle.write(sym + "\n"); _ck_handle.flush()
        _os.fsync(_ck_handle.fileno())

def read_checkpoint() -> Set[str]:
    try:    return set(open(CHECKFILE).read().splitlines())
    except FileNotFoundError: return set()

def mark_failure(sym: str):
    with open(FAILFILE, "a") as f:
        f.write(sym + "\n")

# ──────────────── 5) Alpha Vantage helpers (async) ─────────────────
BASE_URL     = "https://www.alphavantage.co/query"
RATE_LIMITER = AsyncLimiter(CALLS_PER_MIN, 60)

def date_to_yyyymm(d: dt.date) -> int: return d.year * 100 + d.month

async def av_get(session: aiohttp.ClientSession, **params):
    """Generic AV GET; returns JSON dict or raw text depending on response."""
    params |= {"apikey": API_KEY}
    async with RATE_LIMITER:
        try:
            async with session.get(BASE_URL, params=params, timeout=45) as r:
                if r.status != 200: return None
                ct = r.headers.get("Content-Type","")
                if "json" in ct:
                    return await r.json(content_type=None)
                return await r.text()
        except (aiohttp.ClientError, asyncio.TimeoutError):
            return None

async def listing(session: aiohttp.ClientSession, state: str, max_retries: int = 6) -> List[str]:
    """Robust LISTING_STATUS (CSV) with backoff; returns list of stock symbols."""
    params = {"function":"LISTING_STATUS","state":state,"datatype":"csv","apikey":API_KEY}
    backoff = 2
    for attempt in range(1, max_retries+1):
        async with RATE_LIMITER:
            try:
                async with session.get(BASE_URL, params=params, timeout=45) as resp:
                    status = resp.status
                    txt = await resp.text()
            except (aiohttp.ClientError, asyncio.TimeoutError):
                _tqdmw(f"⚠️ LISTING_STATUS {state}: network error (try {attempt})")
                await asyncio.sleep(backoff); backoff *= 2; continue
        if txt.lstrip().startswith("{"):
            try: j = json.loads(txt)
            except json.JSONDecodeError: j = {}
            msg = j.get("Note") or j.get("Information") or j.get("Error Message") or f"HTTP {status}"
            _tqdmw(f"⚠️ LISTING_STATUS {state}: {msg} (try {attempt})")
            await asyncio.sleep(backoff); backoff = min(backoff*2, 30); continue
        rdr = csv.DictReader(io.StringIO(txt))
        syms = [r["symbol"] for r in rdr if r.get("assetType")=="Stock" and r.get("symbol")]
        if syms: return syms
        _tqdmw(f"⚠️ LISTING_STATUS {state}: empty CSV (try {attempt})")
        await asyncio.sleep(backoff); backoff *= 2
    _tqdmw(f"❗ LISTING_STATUS {state}: giving up after {max_retries} attempts")
    return []

async def fetch_balance_sheets(session: aiohttp.ClientSession, sym: str) -> pd.DataFrame | None:
    """Return DataFrame of ALL (annual + quarterly) balance-sheet snapshots with shares."""
    data = await av_get(session, function="BALANCE_SHEET", symbol=sym)
    if not data: return None
    reports = (data.get("annualReports", []) + data.get("quarterlyReports", []))
    if not reports: return None
    df = pd.DataFrame(reports)
    if "commonStockSharesOutstanding" not in df.columns: return None
    df = df.replace({"None": pd.NA, "null": pd.NA, "": pd.NA})
    df = df[df["commonStockSharesOutstanding"].notna()]
    if df.empty: return None

    df["symbol"]           = sym
    df["fiscalDateEnding"] = pd.to_datetime(df["fiscalDateEnding"]).dt.date
    df["reportedCurrency"] = df.get("reportedCurrency", pd.NA)
    df["commonStockSharesOutstanding"] = pd.to_numeric(df["commonStockSharesOutstanding"], errors="coerce")
    df["yyyymm"]           = df["fiscalDateEnding"].map(date_to_yyyymm)

    return df[["symbol","fiscalDateEnding","reportedCurrency","commonStockSharesOutstanding","yyyymm"]]

async def fetch_price_series(session: aiohttp.ClientSession, sym: str, retries=1) -> pd.Series | None:
    """
    Return a Series of adjusted_close indexed by DATE (normalize to midnight).
    Retries once on JSON throttle.
    """
    txt = await av_get(session,
                       function="TIME_SERIES_DAILY_ADJUSTED",
                       symbol=sym,
                       outputsize="full",
                       datatype="csv")

    # Throttle/error returns JSON dict
    if isinstance(txt, dict):
        if retries:
            await asyncio.sleep(60)
            return await fetch_price_series(session, sym, retries-1)
        return None

    if not txt or txt.lstrip().startswith("{"):
        return None

    df = pd.read_csv(io.StringIO(txt), parse_dates=["timestamp"])
    # Normalize index to date (remove time) so lookups by dt.date work reliably
    df["date"] = df["timestamp"].dt.date
    df = df.set_index("date")
    return df["adjusted_close"]

def price_on_or_before(series: pd.Series, target_date: dt.date) -> tuple[dt.date, float] | None:
    """Get last available (date, price) where date <= target_date."""
    if series is None or series.empty: return None
    # Use index slice up to target_date, then take the last row if any.
    try:
        s = series.loc[:target_date]
        if s.size == 0: return None
        d = s.index[-1]
        return d, float(s.iloc[-1])
    except Exception:
        return None

# ───────────────── 6) BigQuery init (partitioned table) ─────────────
try: bq.get_dataset(f"{PROJECT}.{DATASET}")
except gex.NotFound: bq.create_dataset(bigquery.Dataset(f"{PROJECT}.{DATASET}"))

schema = [
    bigquery.SchemaField("symbol","STRING"),
    bigquery.SchemaField("snapshotDate","DATE"),
    bigquery.SchemaField("reportedCurrency","STRING"),
    bigquery.SchemaField("commonStockSharesOutstanding","FLOAT64"),
    bigquery.SchemaField("adjustedClose","FLOAT64"),
    bigquery.SchemaField("marketCap","FLOAT64"),
    bigquery.SchemaField("yyyymm","INT64"),
]
table_ref = f"{PROJECT}.{DATASET}.{TABLE}"
if not any(t.table_id == TABLE for t in bq.list_tables(DATASET)):
    tbl = bigquery.Table(table_ref, schema=schema)
    tbl.range_partitioning = bigquery.RangePartitioning(
        field="yyyymm", range_=bigquery.PartitionRange(PART_START, PART_END, 1))
    tbl.clustering_fields = ["symbol"]
    bq.create_table(tbl)
    _tqdmw(f"➡️  Created table {table_ref}")

CSV_COLS = [f.name for f in bq.get_table(table_ref).schema]

def load_to_bq(df: pd.DataFrame, yyyymm: int, retries: int = 4):
    """Append rows to the specific partition (table$yyyymm)."""
    if df is None or df.empty: return
    df = df.reindex(columns=CSV_COLS)
    fd, tmp = tempfile.mkstemp(suffix=".csv.gz"); _os.close(fd)
    df.to_csv(tmp, index=False, compression="gzip", date_format="%Y-%m-%d")

    dest = f"{table_ref}${yyyymm}"
    cfg = bigquery.LoadJobConfig(
        source_format=bigquery.SourceFormat.CSV,
        skip_leading_rows=1,
        write_disposition="WRITE_APPEND",
    )
    backoff = 5
    for attempt in range(1, retries+1):
        try:
            with open(tmp, "rb") as fh:
                job = bq.load_table_from_file(fh, dest, job_config=cfg, rewind=True)
            _tqdmw(f"⬆️  load {dest} rows {len(df)} (try {attempt})")
            job.result(timeout=300)
            _tqdmw(f"✅ partition {yyyymm} rows {len(df)}")
            break
        except (gex.GoogleAPICallError, gex.RetryError, TimeoutError) as e:
            _tqdmw(f"⚠️  {dest} {e} — backoff {backoff}s")
            time.sleep(backoff); backoff = min(backoff*2, 60)
    _os.remove(tmp)

def dedupe_partitions(parts: Set[int]):
    """De-dup within each yyyymm on (symbol, snapshotDate)."""
    if not parts:
        _tqdmw("🧹 dedupe: no partitions to process")
        return

    sql = f"""
    -- Loop through each partition p
    FOR p IN (SELECT part FROM UNNEST(@parts) AS part) DO

      -- Build cleaned partition
      CREATE OR REPLACE TEMP TABLE tmp AS
      SELECT * EXCEPT(rn)
      FROM (
        SELECT
          t.*,
          ROW_NUMBER() OVER (
            PARTITION BY symbol, snapshotDate
            ORDER BY yyyymm DESC
          ) AS rn
        FROM `{table_ref}` AS t
        WHERE yyyymm = p.part          -- ✅ use p.part here
      )
      WHERE rn = 1;

      -- Replace existing rows for that partition
      DELETE FROM `{table_ref}` WHERE yyyymm = p.part;  -- ✅ and here
      INSERT INTO `{table_ref}` SELECT * FROM tmp;

    END FOR;
    """

    job = bq.query(
        sql,
        job_config=bigquery.QueryJobConfig(
            query_parameters=[
                bigquery.ArrayQueryParameter("parts", "INT64", sorted(parts))
            ]
        ),
    )
    job.result()
    _tqdmw(f"🧹 dedupe: processed {len(parts)} partition(s)")



# ─────────────── 7) Pending buffers + autosave (locked) ────────────
_pending: Dict[int, List[pd.DataFrame]] = defaultdict(list)
_pending_rows: Dict[int, int]           = defaultdict(int)
_part_locks: Dict[int, asyncio.Lock]    = {}

async def flush_partition(part: int):
    lock = _part_locks.setdefault(part, asyncio.Lock())
    async with lock:
        if not _pending[part]:
            return
        batch = pd.concat(_pending[part])
        _pending[part].clear(); _pending_rows[part] = 0
        await asyncio.to_thread(load_to_bq, batch, part)

async def flush_all(tag="💾 flush"):
    tasks = [flush_partition(p) for p,v in list(_pending.items()) if v]
    if tasks:
        _tqdmw(f"{tag}: {len(tasks)} partitions")
        await asyncio.gather(*tasks)

async def auto_flush():
    while True:
        await asyncio.sleep(AUTO_SAVE_SEC)
        await flush_all("⏳ autosave")

# ─────────────────────────── 8) Main driver ────────────────────────
async def main():
    if not API_KEY:
        raise SystemExit("❌  Set ALPHAVANTAGE_API_KEY and retry.")

    done = read_checkpoint()

    connector = aiohttp.TCPConnector(limit=CONCURRENCY)
    async with aiohttp.ClientSession(connector=connector,
                                     timeout=aiohttp.ClientTimeout(total=90)) as session:
        active, delisted = await asyncio.gather(
            listing(session, "active"),
            listing(session, "delisted")
        )
        _tqdmw(f"ℹ️ LISTING_STATUS → active: {len(active):,}, delisted: {len(delisted):,}")
        universe = sorted(set(active + delisted))
        if not universe:
            _tqdmw("❗ LISTING_STATUS returned 0; aborting (premium key expected to work).")
            return

        todo = [s for s in universe if s not in done]
        _tqdmw(f"Universe {len(universe):,} | remaining {len(todo):,}")

        sem  = asyncio.Semaphore(CONCURRENCY)
        pbar = tqdm.tqdm(total=len(todo), desc="Tickers processed", dynamic_ncols=True)
        saver = asyncio.create_task(auto_flush())
        touched_parts: Set[int] = set()

        async def worker(sym: str):
            # Two AV calls per symbol; success-only checkpoint
            async with sem:
                try:
                    bs = await fetch_balance_sheets(session, sym)
                    if bs is None or bs.empty:
                        mark_failure(sym); pbar.update(1); return

                    prices = await fetch_price_series(session, sym)
                    if prices is None or prices.empty:
                        mark_failure(sym); pbar.update(1); return

                    rows = []
                    for _, r in bs.iterrows():
                        report_date: dt.date = r["fiscalDateEnding"]
                        price_hit = price_on_or_before(prices, report_date)
                        if not price_hit:
                            continue
                        snap_date, price = price_hit
                        shares = float(r["commonStockSharesOutstanding"])
                        if pd.isna(shares) or pd.isna(price):  # skip bad rows
                            continue
                        rows.append({
                            "symbol": sym,
                            "snapshotDate": snap_date,
                            "reportedCurrency": r["reportedCurrency"],
                            "commonStockSharesOutstanding": shares,
                            "adjustedClose": float(price),
                            "marketCap": float(price) * float(shares),
                            "yyyymm": date_to_yyyymm(snap_date),
                        })

                    if rows:
                        df = pd.DataFrame(rows).reindex(columns=CSV_COLS)
                        for part, grp in df.groupby("yyyymm"):
                            _pending[part].append(grp)
                            _pending_rows[part] += len(grp)
                            touched_parts.add(int(part))
                            # thresholded flush with lock
                            if _pending_rows[part] >= FLUSH_ROWS:
                                await flush_partition(part)
                        await mark_done(sym)
                    else:
                        mark_failure(sym)
                finally:
                    pbar.update(1)

        await asyncio.gather(*(asyncio.create_task(worker(s)) for s in todo))
        await flush_all("✅ final")
        saver.cancel()
        pbar.close()

    # End-of-run de-dup only for partitions we touched
    await asyncio.to_thread(dedupe_partitions, touched_parts)

# ─────────────────────────── 9) Entry point ────────────────────────
if __name__ == "__main__":
    # Jupyter/Colab friendly: ignore unknown argv
    parser = argparse.ArgumentParser()
    args, _unknown = parser.parse_known_args()
    asyncio.run(main())


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
✅ Checkpoint → /content/drive/MyDrive/alpha_vantage_ckpt/av_done_market_cap2.txt
ℹ️ LISTING_STATUS → active: 7,867, delisted: 7,347
Universe 14,827 | remaining 14,827


Tickers processed:   4%|▍         | 580/14827 [05:00<2:48:54,  1.41it/s]

⏳ autosave: 190 partitions


Tickers processed:   4%|▍         | 583/14827 [05:01<2:28:09,  1.60it/s]

⬆️  load fluid-terminal-465516-s7.magic_formula.market_cap$202112 rows 144 (try 1)
⬆️  load fluid-terminal-465516-s7.magic_formula.market_cap$202103 rows 81 (try 1)
⬆️  load fluid-terminal-465516-s7.magic_formula.market_cap$202109 rows 73 (try 1)
⬆️  load fluid-terminal-465516-s7.magic_formula.market_cap$202012 rows 110 (try 1)
⬆️  load fluid-terminal-465516-s7.magic_formula.market_cap$202203 rows 67 (try 1)


...

✅ partition 201704 rows 17


Tickers processed: 23620it [4:38:52,  1.23it/s]

✅ partition 201709 rows 13


Tickers processed: 23620it [4:38:52,  1.41it/s]


✅ partition 201209 rows 35
🧹 dedupe: processed 281 partition(s)


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
alpha_vantage_company_overview.py — COMPANY-OVERVIEW (premium) ✅ v1.2

• Fetches Alpha Vantage OVERVIEW (company metadata) for US stocks (active + delisted).
• Partitioned by yyyymm (month of fetch). Writes with WRITE_APPEND, then de-dups.
• Modes:
    full     → all symbols
    gapfill  → symbols missing for current yyyymm
    backfill → symbols already present for current yyyymm (refresh), then de-dup
    auto     → full if current month empty else gapfill
• Premium friendly: CALLS_PER_MIN=75, CONCURRENCY=50, async + rate-limited.
"""

# ───────────────────────────── CONFIG ───────────────────────────────
PROJECT   = "fluid-terminal-465516-s7"
DATASET   = "magic_formula"
TABLE     = "company_overview"

import os as _os
API_KEY   = 'IXNJPOSFX5OJYYQD' # REQUIRED

CALLS_PER_MIN = 75
CONCURRENCY   = 50
FLUSH_ROWS    = 5_000
CHECKFILE     = "av_done_symbols_co.txt"
FAILFILE      = "av_failed_symbols_co.txt"
PART_START, PART_END = 198001, 204001  # yyyymm

# ───────────────────────────── IMPORTS ──────────────────────────────
import io, csv, json, time, asyncio, tempfile, aiohttp, nest_asyncio, argparse, datetime
from collections import defaultdict
from typing import Dict, List, Set, Tuple
import pandas as pd
import requests
import tqdm

from aiolimiter import AsyncLimiter
from google.cloud import bigquery
from google.api_core import exceptions as gex
from google.auth.exceptions import DefaultCredentialsError, RefreshError
from google.oauth2 import service_account

nest_asyncio.apply()

# ───────────────────────── Auth-robust BigQuery client ──────────────
def get_bq_client() -> bigquery.Client:
    # 1) Colab/Notebook user auth
    try:
        from google.colab import auth as colab_auth  # type: ignore
        colab_auth.authenticate_user()
        return bigquery.Client(project=PROJECT)
    except Exception:
        pass
    # 2) Service account
    sa_path = _os.getenv("GOOGLE_APPLICATION_CREDENTIALS")
    if sa_path and _os.path.exists(sa_path):
        creds = service_account.Credentials.from_service_account_file(sa_path)
        return bigquery.Client(project=PROJECT, credentials=creds)
    # 3) ADC (gcloud)
    try:
        return bigquery.Client(project=PROJECT)
    except (DefaultCredentialsError, RefreshError) as e:
        raise RuntimeError(
            "No Google Cloud credentials found. Use Colab auth, a service account "
            "via GOOGLE_APPLICATION_CREDENTIALS, or `gcloud auth application-default login`."
        ) from e

bq = get_bq_client()

# ───────────────────── Alpha Vantage async helpers ──────────────────
BASE_URL     = "https://www.alphavantage.co/query"
RATE_LIMITER = AsyncLimiter(CALLS_PER_MIN, 60)

async def av_request(session: aiohttp.ClientSession, params: dict) -> dict | None:
    """Generic AV GET with rate limiting & error handling."""
    async with RATE_LIMITER:
        try:
            async with session.get(BASE_URL, params=params, timeout=45) as resp:
                if resp.status != 200:
                    return None
                return await resp.json(content_type=None)
        except (aiohttp.ClientError, asyncio.TimeoutError):
            return None

async def listing(session: aiohttp.ClientSession, state: str, max_retries: int = 6) -> List[str]:
    """Robust LISTING_STATUS CSV → list of stock symbols."""
    params = {"function": "LISTING_STATUS", "state": state, "datatype": "csv", "apikey": API_KEY}
    backoff = 2
    for attempt in range(1, max_retries + 1):
        async with RATE_LIMITER:
            try:
                async with session.get(BASE_URL, params=params, timeout=45) as resp:
                    status = resp.status
                    txt = await resp.text()
            except (aiohttp.ClientError, asyncio.TimeoutError):
                tqdm.tqdm.write(f"⚠️ LISTING_STATUS {state}: network error (try {attempt})")
                await asyncio.sleep(backoff); backoff *= 2
                continue

        if txt.lstrip().startswith("{"):
            # Quota/info JSON even with 200 OK
            try:
                j = json.loads(txt)
            except json.JSONDecodeError:
                j = {}
            msg = j.get("Note") or j.get("Information") or j.get("Error Message") or f"HTTP {status}"
            tqdm.tqdm.write(f"⚠️ LISTING_STATUS {state}: {msg} (try {attempt})")
            await asyncio.sleep(backoff); backoff = min(backoff * 2, 30)
            continue

        rdr = csv.DictReader(io.StringIO(txt))
        syms = [r["symbol"] for r in rdr if r.get("assetType") == "Stock" and r.get("symbol")]
        if syms:
            return syms

        tqdm.tqdm.write(f"⚠️ LISTING_STATUS {state}: empty CSV (try {attempt})")
        await asyncio.sleep(backoff); backoff *= 2

    tqdm.tqdm.write(f"❗ LISTING_STATUS {state}: giving up after {max_retries} attempts")
    return []

# ─────────────────────── Overview fetch & shaping ───────────────────
TODAY        = datetime.date.today()
FETCH_YYYYMM = TODAY.year * 100 + TODAY.month

def coerce_numeric(col: pd.Series) -> pd.Series:
    col = col.replace({"None": pd.NA, "null": pd.NA, "": pd.NA})
    return pd.to_numeric(col, errors="coerce")

async def fetch_overview(session: aiohttp.ClientSession, sym: str) -> pd.DataFrame | None:
    """Return a one-row DataFrame with selected overview fields for *sym*."""
    data = await av_request(session, {"function": "OVERVIEW", "symbol": sym, "apikey": API_KEY})
    # Alpha Vantage returns {} for unknown symbols
    if not data or "Symbol" not in data:
        return None

    keep_map = {
        "Symbol": "symbol",
        "MarketCapitalization": "marketCap",
        "PERatio": "peRatio",
        "Sector": "sector",
        "Industry": "industry",
        "Country": "country",
    }
    row = {new: data.get(old) for old, new in keep_map.items()}
    row["yyyymm"] = FETCH_YYYYMM
    df = pd.DataFrame([row])
    # numeric casts
    for c in ["marketCap", "peRatio"]:
        if c in df.columns:
            df[c] = coerce_numeric(df[c])
    return df

# ───────────────────────── BigQuery boot-strapping ──────────────────
# Dataset
try:
    bq.get_dataset(f"{PROJECT}.{DATASET}")
except gex.NotFound:
    bq.create_dataset(bigquery.Dataset(f"{PROJECT}.{DATASET}"))

table_ref = f"{PROJECT}.{DATASET}.{TABLE}"

SCHEMA = [
    bigquery.SchemaField("symbol",    "STRING"),
    bigquery.SchemaField("marketCap", "FLOAT64"),
    bigquery.SchemaField("peRatio",   "FLOAT64"),
    bigquery.SchemaField("sector",    "STRING"),
    bigquery.SchemaField("industry",  "STRING"),
    bigquery.SchemaField("country",   "STRING"),
    bigquery.SchemaField("yyyymm",    "INT64"),
]

def ensure_table():
    try:
        tbl = bq.get_table(table_ref)
        existing = {f.name for f in tbl.schema}
        need = [f for f in SCHEMA if f.name not in existing]
        if need:
            tbl.schema += need
            bq.update_table(tbl, ["schema"])
            tqdm.tqdm.write(f"🆕 added missing columns → {', '.join(f.name for f in need)}")
    except gex.NotFound:
        tbl = bigquery.Table(table_ref, schema=SCHEMA)
        tbl.range_partitioning = bigquery.RangePartitioning(
            field="yyyymm", range_=bigquery.PartitionRange(PART_START, PART_END, 1)
        )
        tbl.clustering_fields = ["symbol"]
        bq.create_table(tbl)
        tqdm.tqdm.write(f"➡️  created table {table_ref}")

ensure_table()
CSV_COLS = [f.name for f in bq.get_table(table_ref).schema]  # keep order consistent

# ───────────────────────── Load & Dedupe helpers ────────────────────
def load_partition(df_part: pd.DataFrame, yyyymm: int, retries: int = 4):
    """Append df_part to TABLE$yyyymm via gzip CSV."""
    if df_part is None or df_part.empty:
        return
    df_part = df_part.reindex(columns=CSV_COLS)
    fd, tmp = tempfile.mkstemp(suffix=".csv.gz"); _os.close(fd)
    df_part.to_csv(tmp, index=False, compression="gzip", date_format="%Y-%m-%d")

    dest = f"{table_ref}${yyyymm}"  # explicitly target this partition
    cfg = bigquery.LoadJobConfig(
        source_format=bigquery.SourceFormat.CSV,
        skip_leading_rows=1,
        write_disposition="WRITE_APPEND",
    )
    backoff = 5
    for attempt in range(1, retries + 1):
        try:
            with open(tmp, "rb") as fh:
                job = bq.load_table_from_file(fh, dest, job_config=cfg, rewind=True)
            tqdm.tqdm.write(f"⬆️  load {dest} rows {len(df_part)} (try {attempt})")
            job.result(timeout=300)
            tqdm.tqdm.write(f"✅ partition {yyyymm} rows {len(df_part)}")
            break
        except (gex.GoogleAPICallError, gex.RetryError, TimeoutError) as e:
            tqdm.tqdm.write(f"⚠️  {dest} {e} — backoff {backoff}s")
            time.sleep(backoff); backoff = min(backoff * 2, 60)
    _os.remove(tmp)

def dedupe_month(yyyymm: int):
    """Keep one row per (symbol, yyyymm)."""
    sql = f"""
    CREATE OR REPLACE TEMP TABLE tmp AS
    SELECT * EXCEPT(rn) FROM (
      SELECT t.*,
             ROW_NUMBER() OVER (
               PARTITION BY symbol, yyyymm
               ORDER BY symbol
             ) rn
      FROM `{table_ref}` t
      WHERE yyyymm = @p
    )
    WHERE rn = 1;

    DELETE FROM `{table_ref}` WHERE yyyymm = @p;
    INSERT INTO `{table_ref}` SELECT * FROM tmp;
    """
    job = bq.query(
        sql,
        job_config=bigquery.QueryJobConfig(
            query_parameters=[bigquery.ScalarQueryParameter("p", "INT64", yyyymm)]
        ),
    )
    job.result()
    tqdm.tqdm.write(f"🧹 dedupe complete for {yyyymm}")

# ───────────────────────── Checkpoint / symbols ─────────────────────
def read_checkpoint() -> Set[str]:
    return set(open(CHECKFILE).read().splitlines()) if _os.path.exists(CHECKFILE) else set()

def add_checkpoint(sym: str):
    with open(CHECKFILE, "a") as f:
        f.write(sym + "\n")

def add_failure(sym: str):
    with open(FAILFILE, "a") as f:
        f.write(sym + "\n")

def symbols_loaded_for_month(yyyymm: int) -> Set[str]:
    q = f"SELECT DISTINCT symbol FROM `{table_ref}` WHERE yyyymm = @p"
    rows = bq.query(q, job_config=bigquery.QueryJobConfig(
        query_parameters=[bigquery.ScalarQueryParameter("p", "INT64", yyyymm)]
    )).result()
    return {r.symbol for r in rows}

# ───────────────────────── Mode selection helper ────────────────────
def decide_mode(requested: str, existing_for_month: Set[str], universe: List[str]) -> str:
    if requested != "auto":
        return requested
    if not existing_for_month:
        tqdm.tqdm.write("🧭 Auto: current month empty → FULL")
        return "full"
    tqdm.tqdm.write("🧭 Auto: current month has data → GAP-FILL")
    return "gapfill"

# ───────────────────────── Main async entry-point ───────────────────
async def run(mode: str):
    if not API_KEY:
        raise SystemExit("❌ Set ALPHAVANTAGE_API_KEY and retry.")

    pending: List[pd.DataFrame] = []
    sem       = asyncio.Semaphore(CONCURRENCY)
    connector = aiohttp.TCPConnector(limit=CONCURRENCY)

    async with aiohttp.ClientSession(connector=connector,
                                     timeout=aiohttp.ClientTimeout(total=90)) as session:
        active, delisted = await asyncio.gather(
            listing(session, "active"),
            listing(session, "delisted"),
        )
        tqdm.tqdm.write(f"ℹ️ LISTING_STATUS → active: {len(active):,}, delisted: {len(delisted):,}")
        universe = sorted(set(active + delisted))
        if not universe:
            tqdm.tqdm.write("❗ LISTING_STATUS returned 0; aborting (premium key expected to work).")
            return

        existing_month = symbols_loaded_for_month(FETCH_YYYYMM)
        mode = decide_mode(mode, existing_month, universe)

        if mode == "full":
            todo = universe
            desc = "FULL crawl (overview)"
        elif mode == "gapfill":
            todo = [s for s in universe if s not in existing_month]
            desc = "GAP-FILL (missing for current month)"
        elif mode == "backfill":
            todo = [s for s in universe if s in existing_month]
            desc = "BACKFILL (already present this month)"
        else:
            raise SystemExit(f"Unknown mode: {mode}")

        # (Optional) also factor in historical success checkpoint if you want resume semantics
        done = read_checkpoint()
        # Only skip by checkpoint for full/backfill; for gapfill we already filtered by BQ presence
        if mode in ("full", "backfill"):
            todo = [s for s in todo if s not in done]

        tqdm.tqdm.write(f"Mode: {desc} | universe {len(universe):,} | "
                        f"in-month {len(existing_month):,} | to fetch {len(todo):,}")

        pbar = tqdm.tqdm(total=len(todo), desc="Symbols processed", dynamic_ncols=True)

        async def worker(sym: str):
            async with sem:
                df = await fetch_overview(session, sym)
                if df is not None and not df.empty:
                    pending.append(df)
                    # flush on threshold (single month partition)
                    if sum(len(d) for d in pending) >= FLUSH_ROWS:
                        batch = pd.concat(pending); pending.clear()
                        await asyncio.to_thread(load_partition, batch, FETCH_YYYYMM)
                    add_checkpoint(sym)  # success-only
                else:
                    add_failure(sym)
                pbar.update(1)

        await asyncio.gather(*(asyncio.create_task(worker(s)) for s in todo))
        pbar.close()

    # Final flush
    if pending:
        await asyncio.to_thread(load_partition, pd.concat(pending), FETCH_YYYYMM)

    # De-dup the current month
    await asyncio.to_thread(dedupe_month, FETCH_YYYYMM)

# ────────────────────────────────────────────────────────────────────
if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    parser.add_argument("--mode", choices=["auto", "full", "gapfill", "backfill"],
                        default="auto",
                        help="auto=full if current month empty else gap-fill")
    args, _unknown = parser.parse_known_args()  # Jupyter-friendly
    asyncio.run(run(args.mode))


ℹ️ LISTING_STATUS → active: 7,852, delisted: 7,343
🧭 Auto: current month empty → FULL
Mode: FULL crawl (overview) | universe 14,809 | in-month 0 | to fetch 14,809


Symbols processed:  72%|███████▏  | 10677/14809 [2:21:23<1:01:07,  1.13it/s]

⬆️  load fluid-terminal-465516-s7.magic_formula.company_overview$202512 rows 5000 (try 1)


Symbols processed:  72%|███████▏  | 10680/14809 [2:21:24<44:12,  1.56it/s]

✅ partition 202512 rows 5000


Symbols processed: 100%|██████████| 14809/14809 [3:16:27<00:00,  1.26it/s]


⬆️  load fluid-terminal-465516-s7.magic_formula.company_overview$202512 rows 1983 (try 1)
✅ partition 202512 rows 1983
🧹 dedupe complete for 202512


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
alpha_vantage_income_statement_full.py — INCOME-STATEMENT (premium) ✅ v4.0

• Quarterly income statements for US stocks (active + delisted).
• Modes:
    full     → all symbols
    gapfill  → symbols missing from BQ
    backfill → symbols already in BQ (row-level backfill; end-of-run de-dup)
• Premium-friendly: CALLS_PER_MIN=75, CONCURRENCY=50, robust async LISTING_STATUS.
• Dynamic schema discovery + auto-evolve (incl. mid-run).
• Safe CSV loads (column-order alignment, mkstemp, WRITE_APPEND to partitions).
• Success-only checkpoint + failure log.
• Per-partition flush locks; end-of-run de-dup on (symbol, fiscalDateEnding).
• Jupyter-friendly CLI (parse_known_args).

Env:
  ALPHAVANTAGE_API_KEY  (required)
  GOOGLE_APPLICATION_CREDENTIALS (optional, path to service account JSON)
"""

# ───────────────────────────── CONFIG ───────────────────────────────
PROJECT   = "fluid-terminal-465516-s7"
DATASET   = "magic_formula"
TABLE     = "income_statement"   # same table name, now quarterly data

import os as _os
API_KEY   = 'IXNJPOSFX5OJYYQD' # REQUIRED

CALLS_PER_MIN = 75
CONCURRENCY   = 50
FLUSH_ROWS    = 10_000
CHECKFILE     = "av_done_symbols_is.txt"
FAILFILE      = "av_failed_symbols_is.txt"
PART_START, PART_END = 198001, 204001  # yyyymm partition range

# ───────────────────────────── IMPORTS ──────────────────────────────
import io, csv, json, time, asyncio, tempfile, aiohttp, nest_asyncio, argparse
from collections import defaultdict
from typing import Dict, List, Set, Tuple
import pandas as pd
import requests
import tqdm                      # module-style import
from aiolimiter import AsyncLimiter

from google.cloud import bigquery
from google.api_core import exceptions as gex
from google.auth.exceptions import DefaultCredentialsError, RefreshError
from google.oauth2 import service_account

nest_asyncio.apply()

# ───────────────────────── Auth-robust BigQuery client ──────────────
def get_bq_client() -> bigquery.Client:
    try:
        from google.colab import auth as colab_auth  # type: ignore
        colab_auth.authenticate_user()
        return bigquery.Client(project=PROJECT)
    except Exception:
        pass
    sa_path = _os.getenv("GOOGLE_APPLICATION_CREDENTIALS")
    if sa_path and _os.path.exists(sa_path):
        creds = service_account.Credentials.from_service_account_file(sa_path)
        return bigquery.Client(project=PROJECT, credentials=creds)
    try:
        return bigquery.Client(project=PROJECT)
    except (DefaultCredentialsError, RefreshError) as e:
        raise RuntimeError(
            "No Google Cloud credentials found. Do one of:\n"
            "  • Colab: from google.colab import auth; auth.authenticate_user()\n"
            "  • Service account: set GOOGLE_APPLICATION_CREDENTIALS to your JSON path\n"
            "  • gcloud: run `gcloud auth application-default login`"
        ) from e

bq = get_bq_client()

# ─────────────────── Alpha Vantage helpers (async) ──────────────────
BASE_URL     = "https://www.alphavantage.co/query"
RATE_LIMITER = AsyncLimiter(CALLS_PER_MIN, 60)

async def av_request(session: aiohttp.ClientSession, params: dict) -> dict | None:
    async with RATE_LIMITER:
        try:
            async with session.get(BASE_URL, params=params, timeout=45) as resp:
                if resp.status != 200:
                    return None
                return await resp.json(content_type=None)
        except (aiohttp.ClientError, asyncio.TimeoutError):
            return None

async def listing(session: aiohttp.ClientSession, state: str, max_retries: int = 6) -> List[str]:
    params = {"function": "LISTING_STATUS", "state": state, "datatype": "csv", "apikey": API_KEY}
    backoff = 2
    for attempt in range(1, max_retries + 1):
        async with RATE_LIMITER:
            try:
                async with session.get(BASE_URL, params=params, timeout=45) as resp:
                    status = resp.status
                    txt = await resp.text()
            except (aiohttp.ClientError, asyncio.TimeoutError):
                tqdm.tqdm.write(f"⚠️ LISTING_STATUS {state}: network error (try {attempt})")
                await asyncio.sleep(backoff); backoff *= 2
                continue
        if txt.lstrip().startswith("{"):
            try:
                j = json.loads(txt)
            except json.JSONDecodeError:
                j = {}
            msg = j.get("Note") or j.get("Information") or j.get("Error Message") or f"HTTP {status}"
            tqdm.tqdm.write(f"⚠️ LISTING_STATUS {state}: {msg} (try {attempt})")
            await asyncio.sleep(backoff); backoff = min(backoff * 2, 30)
            continue
        rdr = csv.DictReader(io.StringIO(txt))
        syms = [r["symbol"] for r in rdr if r.get("assetType") == "Stock" and r.get("symbol")]
        if syms:
            return syms
        tqdm.tqdm.write(f"⚠️ LISTING_STATUS {state}: empty CSV (try {attempt})")
        await asyncio.sleep(backoff); backoff *= 2
    tqdm.tqdm.write(f"❗ LISTING_STATUS {state}: giving up after {max_retries} attempts")
    return []

def coerce_numeric(col: pd.Series) -> pd.Series:
    col = col.replace({"None": pd.NA, "null": pd.NA, "": pd.NA})
    return pd.to_numeric(col, errors="coerce")

# ─────────────── fetch QUARTERLY income statement here ──────────────
async def fetch_income_statement(session: aiohttp.ClientSession, sym: str) -> pd.DataFrame | None:
    data = await av_request(
        session,
        {"function": "INCOME_STATEMENT", "symbol": sym, "apikey": API_KEY}
    )
    # use quarterlyReports instead of annualReports
    if not data or not data.get("quarterlyReports"):
        return None

    df = pd.DataFrame(data["quarterlyReports"])
    df["symbol"] = sym

    # SG&A alias normalization
    if "sellingGeneralAndAdministrative" in df.columns and "sellingGeneralAdministrative" not in df.columns:
        df["sellingGeneralAdministrative"] = df["sellingGeneralAndAdministrative"]

    df["fiscalDateEnding"] = pd.to_datetime(df["fiscalDateEnding"]).dt.date
    df["yyyymm"] = df["fiscalDateEnding"].apply(lambda d: d.year * 100 + d.month).astype("int64")

    non_numeric = {"symbol", "fiscalDateEnding", "reportedCurrency", "yyyymm"}
    numeric_cols = [c for c in df.columns if c not in non_numeric]
    if numeric_cols:
        df[numeric_cols] = df[numeric_cols].apply(coerce_numeric)
    return df

# ───────────────────── BigQuery boot-strapping ─────────────────────
try:
    bq.get_dataset(f"{PROJECT}.{DATASET}")
except gex.NotFound:
    bq.create_dataset(bigquery.Dataset(f"{PROJECT}.{DATASET}"))

table_ref = f"{PROJECT}.{DATASET}.{TABLE}"

SAMPLE_TICKERS = ["AAPL", "IBM", "MSFT", "XOM", "GE", "GOOGL", "AMZN", "BAC"]

def discover_fields(sample_syms: List[str]) -> List[str]:
    """
    Discover all possible fields from both annual and quarterly income statements
    for a small sample of symbols, so our schema covers everything upfront.
    """
    fields: Set[str] = set()
    for sym in sample_syms:
        try:
            resp = requests.get(
                BASE_URL,
                params={"function": "INCOME_STATEMENT", "symbol": sym, "apikey": API_KEY},
                timeout=20
            ).json()
            # include both, in case quarterlyReports has extra keys
            fields |= {k for rpt in resp.get("annualReports", []) for k in rpt}
            fields |= {k for rpt in resp.get("quarterlyReports", []) for k in rpt}
        except Exception:
            continue
        if len(fields) >= 80:
            break
    if "sellingGeneralAndAdministrative" in fields and "sellingGeneralAdministrative" not in fields:
        fields.add("sellingGeneralAdministrative")
    base = ["symbol", "fiscalDateEnding", "reportedCurrency", "yyyymm"]
    return base + sorted(fields - set(base))

FIELDS = discover_fields(SAMPLE_TICKERS)

# ─────────────── FLOAT fix for problematic numeric fields ───────────
_TYPE_OVERRIDES = {
    "symbol": "STRING",
    "fiscalDateEnding": "DATE",
    "reportedCurrency": "STRING",
    "yyyymm": "INT64",
    # IMPORTANT: use FLOAT64 to avoid CSV "1234.0" → INT64 parse errors
    "commonStockSharesOutstanding": "FLOAT64",
}

SCHEMA = [bigquery.SchemaField(col, _TYPE_OVERRIDES.get(col, "FLOAT64")) for col in FIELDS]

def ensure_table() -> Tuple[bool, List[str]]:
    try:
        tbl = bq.get_table(table_ref)
        existing = {f.name for f in tbl.schema}
        missing = [c for c in FIELDS if c not in existing]
        if missing:
            tbl.schema += [bigquery.SchemaField(c, _TYPE_OVERRIDES.get(c, "FLOAT64")) for c in missing]
            bq.update_table(tbl, ["schema"])
            tqdm.tqdm.write(
                f"🆕 Added {len(missing)} new columns → {', '.join(missing[:6])}"
                f"{'…' if len(missing)>6 else ''}"
            )
            return True, missing
        return False, []
    except gex.NotFound:
        tbl = bigquery.Table(table_ref, schema=SCHEMA)
        tbl.range_partitioning = bigquery.RangePartitioning(
            field="yyyymm", range_=bigquery.PartitionRange(PART_START, PART_END, 1)
        )
        tbl.clustering_fields = ["symbol"]
        bq.create_table(tbl)
        tqdm.tqdm.write(f"➡️  created table {table_ref} with {len(SCHEMA)} columns")
        return True, [f.name for f in tbl.schema]

schema_changed_initial, _ = ensure_table()
CSV_COLS = [f.name for f in bq.get_table(table_ref).schema]

# ───────────── Mid-run schema evolve if new columns appear ──────────
_schema_lock = asyncio.Lock()
async def ensure_columns_midrun(new_cols: Set[str]) -> bool:
    if not new_cols:
        return False
    async with _schema_lock:
        tbl = bq.get_table(table_ref)
        existing = {f.name for f in tbl.schema}
        to_add = [c for c in new_cols if c not in existing]
        if not to_add:
            return False
        tbl.schema += [bigquery.SchemaField(c, _TYPE_OVERRIDES.get(c, "FLOAT64")) for c in to_add]
        bq.update_table(tbl, ["schema"])
        global CSV_COLS
        CSV_COLS = [f.name for f in bq.get_table(table_ref).schema]
        tqdm.tqdm.write(f"🆕 (mid-run) added {len(to_add)} cols → {', '.join(to_add)}")
        return True

# ───────────────────── Load helper (partitioned) ───────────────────
def load_partition(df_part: pd.DataFrame, yyyymm: int, retries: int = 4):
    if df_part is None or df_part.empty:
        return
    df_part = df_part.reindex(columns=CSV_COLS)
    fd, tmp = tempfile.mkstemp(suffix=".csv.gz"); _os.close(fd)
    df_part.to_csv(tmp, index=False, compression="gzip", date_format="%Y-%m-%d")
    dest = f"{table_ref}${yyyymm}"
    cfg = bigquery.LoadJobConfig(
        source_format=bigquery.SourceFormat.CSV,
        skip_leading_rows=1,
        write_disposition="WRITE_APPEND",
    )
    backoff = 5
    for attempt in range(1, retries + 1):
        try:
            with open(tmp, "rb") as fh:
                job = bq.load_table_from_file(fh, dest, job_config=cfg, rewind=True)
            tqdm.tqdm.write(f"⬆️  load {dest} rows {len(df_part)} (try {attempt})")
            job.result(timeout=300)
            tqdm.tqdm.write(f"✅ partition {yyyymm} rows {len(df_part)}")
            break
        except (gex.GoogleAPICallError, gex.RetryError, TimeoutError) as e:
            tqdm.tqdm.write(f"⚠️  {dest} {e} — backoff {backoff}s")
            time.sleep(backoff); backoff = min(backoff * 2, 60)
    _os.remove(tmp)

# ───────────────────── Checkpoint / failure helpers ─────────────────
def read_checkpoint() -> Set[str]:
    return set(open(CHECKFILE).read().splitlines()) if _os.path.exists(CHECKFILE) else set()

def add_checkpoint(sym: str):
    with open(CHECKFILE, "a") as f:
        f.write(sym + "\n")

def add_failure(sym: str):
    with open(FAILFILE, "a") as f:
        f.write(sym + "\n")

# ───────────────────────── De-duplication helper ────────────────────
def dedupe_partitions(parts: Set[int]):
    import tqdm as _tqdm
    if not parts:
        _tqdm.tqdm.write("🧹 dedupe: no partitions to process")
        return

    sql = f"""
    FOR part IN (SELECT p FROM UNNEST(@parts) AS p) DO
      CREATE OR REPLACE TEMP TABLE tmp AS
      SELECT * EXCEPT(rn) FROM (
        SELECT t.*,
               ROW_NUMBER() OVER (
                 PARTITION BY symbol, fiscalDateEnding
                 ORDER BY yyyymm DESC
               ) AS rn
        FROM `{table_ref}` AS t
        WHERE yyyymm = part.p      -- ✅ use part.p (struct field)
      )
      WHERE rn = 1;

      DELETE FROM `{table_ref}` WHERE yyyymm = part.p;   -- ✅ use part.p
      INSERT INTO `{table_ref}` SELECT * FROM tmp;
    END FOR;
    """

    job = bq.query(
        sql,
        job_config=bigquery.QueryJobConfig(
            query_parameters=[
                bigquery.ArrayQueryParameter("parts", "INT64", sorted(parts))
            ]
        ),
    )
    job.result()
    _tqdm.tqdm.write(f"🧹 dedupe: processed {len(parts)} partition(s)")

# ───────────────────────── Main async entrypoint ────────────────────
async def run(mode: str):
    if not API_KEY:
        raise SystemExit("❌  Set ALPHAVANTAGE_API_KEY and retry.")

    sem                         = asyncio.Semaphore(CONCURRENCY)
    pending: Dict[int, List[pd.DataFrame]] = defaultdict(list)
    pending_rows: Dict[int, int]           = defaultdict(int)
    part_locks: Dict[int, asyncio.Lock]    = {}
    touched_parts: Set[int]                = set()
    schema_changed_flag: bool              = schema_changed_initial

    async def maybe_flush(part: int):
        lock = part_locks.setdefault(part, asyncio.Lock())
        async with lock:
            if pending_rows[part] >= FLUSH_ROWS:
                batch = pd.concat(pending[part]); pending[part].clear(); pending_rows[part] = 0
                await asyncio.to_thread(load_partition, batch, part)

    connector = aiohttp.TCPConnector(limit=CONCURRENCY)
    async with aiohttp.ClientSession(
        connector=connector,
        timeout=aiohttp.ClientTimeout(total=90)
    ) as session:
        active, delisted = await asyncio.gather(
            listing(session, "active"),
            listing(session, "delisted")
        )
        tqdm.tqdm.write(
            f"ℹ️  LISTING_STATUS → active: {len(active):,}, delisted: {len(delisted):,}"
        )
        universe = sorted(set(active + delisted))
        if not universe:
            tqdm.tqdm.write("❗ LISTING_STATUS returned 0; aborting (premium key expected to work).")
            return

        # Build mode-specific TODO
        existing = {
            row.symbol
            for row in bq.query(f"SELECT DISTINCT symbol FROM `{table_ref}`").result()
        }
        if mode == "auto":
            mode = "full" if len(existing) == 0 else "gapfill"

        if mode == "full":
            todo = universe
            todo_desc = "FULL crawl (quarterly)"
        elif mode == "gapfill":
            todo = [s for s in universe if s not in existing]
            todo_desc = "GAP-FILL (missing symbols only, quarterly)"
        elif mode == "backfill":
            todo = [s for s in universe if s in existing]
            todo_desc = "BACKFILL (existing symbols only, quarterly)"
        else:
            raise SystemExit(f"Unknown mode: {mode}")

        tqdm.tqdm.write(
            f"Mode: {todo_desc} | universe {len(universe):,} | "
            f"already in BQ {len(existing):,} | to fetch {len(todo):,}"
        )

        pbar = tqdm.tqdm(total=len(todo), desc="Symbols processed", dynamic_ncols=True)

        async def worker(sym: str):
            nonlocal schema_changed_flag
            async with sem:
                df = await fetch_income_statement(session, sym)
                if df is None or df.empty:
                    add_failure(sym)
                    pbar.update(1)
                    return

                new_cols = set(df.columns) - set(CSV_COLS)
                if new_cols:
                    changed = await ensure_columns_midrun(new_cols)
                    schema_changed_flag = schema_changed_flag or changed

                for part, grp in df.groupby("yyyymm"):
                    pending[part].append(grp)
                    pending_rows[part] += len(grp)
                    touched_parts.add(int(part))
                    await maybe_flush(part)

                add_checkpoint(sym)  # success-only
                pbar.update(1)

        tasks = [asyncio.create_task(worker(s)) for s in todo]
        await asyncio.gather(*tasks)
        pbar.close()

    # flush any remaining
    for part, dfs in pending.items():
        if dfs:
            await asyncio.to_thread(load_partition, pd.concat(dfs), part)

    # de-dup quarterly rows per (symbol, fiscalDateEnding)
    await asyncio.to_thread(dedupe_partitions, touched_parts)

# ────────────────────────────────────────────────────────────────────
if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    parser.add_argument(
        "--mode",
        choices=["auto", "full", "gapfill", "backfill"],
        default="auto",
        help="auto=full if empty else gap-fill; backfill=existing symbols only",
    )
    args, _unknown = parser.parse_known_args()
    asyncio.run(run(args.mode))


ℹ️  LISTING_STATUS → active: 7,852, delisted: 7,343
Mode: GAP-FILL (missing symbols only, quarterly) | universe 14,809 | already in BQ 6,060 | to fetch 8,749


Symbols processed: 100%|██████████| 8749/8749 [1:55:39<00:00,  1.26it/s]


⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201012 rows 1 (try 1)
✅ partition 201012 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201103 rows 1 (try 1)
✅ partition 201103 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201106 rows 1 (try 1)
✅ partition 201106 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201109 rows 1 (try 1)
✅ partition 201109 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201112 rows 1 (try 1)
✅ partition 201112 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201203 rows 1 (try 1)
✅ partition 201203 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201206 rows 1 (try 1)
✅ partition 201206 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201209 rows 1 (try 1)
✅ partition 201209 rows 1
⬆️  load fluid-terminal-465516-s7.magic_formula.income_statement$201212 rows 1 (try 1)
✅ partiti

In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
alpha_vantage_balance_sheet_quarterly.py — full-crawl OR gap-fill (auto) ✅

• Pulls QUARTERLY balance-sheet data (quarterlyReports) for US stocks (active + delisted).
• Auto mode: full crawl if table empty; otherwise gap-fill (missing symbols).
• Async + rate-limited, WRITE_APPEND to monthly partitions (yyyymm), per-partition flush locks.
• Dynamic schema discovery + auto-evolve (including mid-run if a new column appears).
• Success-only checkpoint; failure log; end-of-run de-dup per touched partition.
• Robust LISTING_STATUS: fetch **once** (no `state`), parse CSV, split on `status`.
• Falls back to a BigQuery-derived universe if LISTING_STATUS returns 0 symbols.
• Jupyter/Colab-friendly CLI: ignores unknown args (e.g., -f kernel.json).

CLI:
  --mode {auto,full,gapfill}     default: auto
  --refetch-on-schema-change     if schema evolves, refetch already-loaded symbols this run

Env:
  ALPHAVANTAGE_API_KEY (required)
  GOOGLE_APPLICATION_CREDENTIALS (optional, path to service account JSON)
"""

# ───────────────────────────── CONFIG ───────────────────────────────
PROJECT     = "fluid-terminal-465516-s7"       # GCP project ID
DATASET     = "magic_formula"                  # BigQuery dataset
TABLE       = "balance_sheet"                # Destination table (quarterly)
CHECKFILE   = "av_done_symbols_balance_q.txt"  # success-only checkpoint
FAILFILE    = "av_failed_symbols_balance_q.txt"

import os as _os
API_KEY     = 'IXNJPOSFX5OJYYQD'  # REQUIRED

CALLS_PER_MIN  = 75                      # Alpha Vantage premium (free=5)
CONCURRENCY    = 50                      # concurrent HTTP requests
FLUSH_ROWS     = 10_000                  # per-partition flush threshold
PART_START, PART_END = 198001, 204001    # RANGE partition (yyyymm)

# ───────────────────────────── IMPORTS ──────────────────────────────
import io, csv, json, time, asyncio, tempfile, aiohttp, nest_asyncio, sys, argparse
from collections import defaultdict
from typing import Dict, List, Set, Tuple
import pandas as pd
import tqdm
import requests
from aiolimiter import AsyncLimiter

from google.cloud import bigquery
from google.api_core import exceptions as gex
from google.auth.exceptions import DefaultCredentialsError, RefreshError
from google.oauth2 import service_account

nest_asyncio.apply()

# ───────────────────────── Auth-robust BigQuery client ──────────────
def get_bq_client() -> bigquery.Client:
    # 1) Colab / Notebook user auth
    try:
        from google.colab import auth as colab_auth  # type: ignore
        colab_auth.authenticate_user()
        return bigquery.Client(project=PROJECT)
    except Exception:
        pass

    # 2) Service account via GOOGLE_APPLICATION_CREDENTIALS
    sa_path = _os.getenv("GOOGLE_APPLICATION_CREDENTIALS")
    if sa_path and _os.path.exists(sa_path):
        creds = service_account.Credentials.from_service_account_file(sa_path)
        return bigquery.Client(project=PROJECT, credentials=creds)

    # 3) Application Default Credentials (gcloud)
    try:
        return bigquery.Client(project=PROJECT)
    except (DefaultCredentialsError, RefreshError) as e:
        raise RuntimeError(
            "No Google Cloud credentials found. Do one of:\n"
            "  • In Colab: from google.colab import auth; auth.authenticate_user()\n"
            "  • With service account: set GOOGLE_APPLICATION_CREDENTIALS to your JSON path\n"
            "  • With gcloud: run `gcloud auth application-default login`"
        ) from e

bq = get_bq_client()

# ───────────────────── Alpha Vantage async fetchers ─────────────────
BASE_URL     = "https://www.alphavantage.co/query"
RATE_LIMITER = AsyncLimiter(CALLS_PER_MIN, 60)

async def av_request(session: aiohttp.ClientSession, params: dict) -> dict | None:
    """Generic AV GET with rate limiting & error handling."""
    async with RATE_LIMITER:
        try:
            async with session.get(BASE_URL, params=params, timeout=45) as resp:
                if resp.status != 200:
                    return None
                return await resp.json(content_type=None)
        except (aiohttp.ClientError, asyncio.TimeoutError):
            return None

async def listing_all(session: aiohttp.ClientSession, max_retries: int = 6) -> Tuple[List[str], List[str]]:
    """
    Robust LISTING_STATUS fetch:
      • Call once (no `state`) with `datatype=csv`.
      • Parse CSV and split rows by `status` into (active, delisted).
      • Retries/backoff on JSON 'Note/Information/Error' or empty CSV.
    """
    params = {"function": "LISTING_STATUS", "datatype": "csv", "apikey": API_KEY}
    backoff = 3

    for attempt in range(1, max_retries + 1):
        async with RATE_LIMITER:
            try:
                async with session.get(BASE_URL, params=params, timeout=45) as resp:
                    status = resp.status
                    txt = await resp.text()
            except (aiohttp.ClientError, asyncio.TimeoutError):
                tqdm.tqdm.write(f"⚠️ LISTING_STATUS: network error (attempt {attempt})")
                await asyncio.sleep(backoff); backoff *= 2
                continue

        # If JSON → quota/error or something unexpected
        if txt.lstrip().startswith("{"):
            try:
                j = json.loads(txt)
            except json.JSONDecodeError:
                j = {}
            msg = j.get("Note") or j.get("Information") or j.get("Error Message") or f"HTTP {status}"
            # Show a small preview too for debugging
            preview = (txt[:160] + "…") if len(txt) > 160 else txt
            tqdm.tqdm.write(f"⚠️ LISTING_STATUS JSON: {msg} (attempt {attempt}) | preview: {preview}")
            await asyncio.sleep(backoff); backoff = min(backoff * 2, 60)
            continue

        # Try to parse CSV
        try:
            rdr = csv.DictReader(io.StringIO(txt))
            act, dels = [], []
            for r in rdr:
                if not r.get("symbol") or r.get("assetType") != "Stock":
                    continue
                status_str = (r.get("status") or "").strip().lower()
                if status_str == "active":
                    act.append(r["symbol"])
                elif status_str == "delisted":
                    dels.append(r["symbol"])
                else:
                    # ignore 'Suspended', 'Unknown', etc.
                    pass
            if act or dels:
                return act, dels
        except Exception as e:
            tqdm.tqdm.write(f"⚠️ LISTING_STATUS: CSV parse error {e} (attempt {attempt})")

        tqdm.tqdm.write(f"⚠️ LISTING_STATUS: empty/invalid CSV (attempt {attempt})")
        await asyncio.sleep(backoff); backoff *= 2

    tqdm.tqdm.write(f"❗ LISTING_STATUS: giving up after {max_retries} attempts")
    return [], []

def coerce_numeric(col: pd.Series) -> pd.Series:
    """Convert strings that look like numbers into floats; keep NA otherwise."""
    col = col.replace({"None": pd.NA, "null": pd.NA, "": pd.NA})
    return pd.to_numeric(col, errors="coerce")

async def fetch_balance_sheet_quarterly(session: aiohttp.ClientSession, sym: str) -> pd.DataFrame | None:
    """Return DataFrame of QUARTERLY balance-sheet rows for *sym*."""
    data = await av_request(session, {"function": "BALANCE_SHEET", "symbol": sym, "apikey": API_KEY})
    if not data or not data.get("quarterlyReports"):
        return None

    df = pd.DataFrame(data["quarterlyReports"])  # one row per fiscal quarter
    df["symbol"] = sym
    df["fiscalDateEnding"] = pd.to_datetime(df["fiscalDateEnding"]).dt.date
    df["yyyymm"] = df["fiscalDateEnding"].apply(lambda d: d.year * 100 + d.month).astype("int64")

    non_numeric = {"symbol", "fiscalDateEnding", "reportedCurrency", "yyyymm"}
    numeric_cols = [c for c in df.columns if c not in non_numeric]
    if numeric_cols:
        df[numeric_cols] = df[numeric_cols].apply(coerce_numeric)
    return df

# ─────────────────── Seed fields (from your provided list) ───────────────────
PROVIDED_FIELDS = [
    "fiscalDateEnding", "reportedCurrency",
    "totalAssets", "totalCurrentAssets", "cashAndCashEquivalentsAtCarryingValue",
    "cashAndShortTermInvestments", "inventory", "currentNetReceivables",
    "totalNonCurrentAssets", "propertyPlantEquipment", "accumulatedDepreciationAmortizationPPE",
    "intangibleAssets", "intangibleAssetsExcludingGoodwill", "goodwill", "investments",
    "longTermInvestments", "shortTermInvestments", "otherCurrentAssets", "otherNonCurrentAssets",
    "totalLiabilities", "totalCurrentLiabilities", "currentAccountsPayable", "deferredRevenue",
    "currentDebt", "shortTermDebt", "totalNonCurrentLiabilities", "capitalLeaseObligations",
    "longTermDebt", "currentLongTermDebt", "longTermDebtNoncurrent", "shortLongTermDebtTotal",
    "otherCurrentLiabilities", "otherNonCurrentLiabilities", "totalShareholderEquity",
    "treasuryStock", "retainedEarnings", "commonStock", "commonStockSharesOutstanding",
]

# ───────────────────────── BigQuery bootstrapping ───────────────────
# Dataset
try:
    bq.get_dataset(f"{PROJECT}.{DATASET}")
except gex.NotFound:
    bq.create_dataset(bigquery.Dataset(f"{PROJECT}.{DATASET}"))

table_ref = f"{PROJECT}.{DATASET}.{TABLE}"

def discover_fields(sample_symbols: list[str]) -> list[str]:
    """Discover quarterly field names by sampling a few diverse tickers."""
    fields: Set[str] = set()
    for sym in sample_symbols:
        try:
            resp = requests.get(
                BASE_URL,
                params={"function": "BALANCE_SHEET", "symbol": sym, "apikey": API_KEY},
                timeout=15
            ).json()
            fields |= {k for rpt in resp.get("quarterlyReports", []) for k in rpt}
        except Exception:
            continue
        if len(fields) >= 60:
            break
    base = ["symbol", "fiscalDateEnding", "reportedCurrency", "yyyymm"]
    return base + sorted((fields | set(PROVIDED_FIELDS)) - set(base))

FIELDS = discover_fields(["AAPL", "IBM", "XOM", "GE", "BAC", "MSFT"])

_TYPE_OVERRIDES = {
    "symbol": "STRING",
    "reportedCurrency": "STRING",
    "fiscalDateEnding": "DATE",
    "yyyymm": "INT64",
    "commonStockSharesOutstanding": "FLOAT64",  # often integral
}
SCHEMA = [bigquery.SchemaField(col, _TYPE_OVERRIDES.get(col, "FLOAT64")) for col in FIELDS]

def ensure_table() -> Tuple[bool, list[str]]:
    """Ensure table exists and has at least FIELDS columns. Returns (schema_changed, missing_added)."""
    try:
        tbl = bq.get_table(table_ref)
        existing_cols = {f.name for f in tbl.schema}
        missing = [c for c in FIELDS if c not in existing_cols]
        if missing:
            tbl.schema += [bigquery.SchemaField(c, _TYPE_OVERRIDES.get(c, "FLOAT64")) for c in missing]
            bq.update_table(tbl, ["schema"])
            tqdm.tqdm.write(f"🆕 added {len(missing)} new columns → {', '.join(missing)}")
            return True, missing
        return False, []
    except gex.NotFound:
        tbl = bigquery.Table(table_ref, schema=SCHEMA)
        tbl.range_partitioning = bigquery.RangePartitioning(
            field="yyyymm",
            range_=bigquery.PartitionRange(PART_START, PART_END, 1),
        )
        tbl.clustering_fields = ["symbol"]
        bq.create_table(tbl)
        tqdm.tqdm.write(f"➡️  created table {table_ref} with {len(SCHEMA)} columns")
        return True, [f.name for f in tbl.schema]

schema_changed_initial, _ = ensure_table()
CSV_COLS = [f.name for f in bq.get_table(table_ref).schema]

# ───────────── Mid-run schema evolve if a ticker returns new columns ─────────
_schema_lock = asyncio.Lock()

async def ensure_columns_midrun(new_cols: Set[str]) -> bool:
    """Add new columns discovered mid-run. Returns True if schema changed."""
    if not new_cols:
        return False
    async with _schema_lock:
        tbl = bq.get_table(table_ref)
        existing = {f.name for f in tbl.schema}
        to_add = [c for c in new_cols if c not in existing]
        if not to_add:
            return False
        tbl.schema += [bigquery.SchemaField(c, _TYPE_OVERRIDES.get(c, "FLOAT64")) for c in to_add]
        bq.update_table(tbl, ["schema"])
        tqdm.tqdm.write(f"🆕 (mid-run) added {len(to_add)} cols → {', '.join(to_add)}")
        global CSV_COLS
        CSV_COLS = [f.name for f in bq.get_table(table_ref).schema]
        return True

# ─────────────────────── Load to a single partition ─────────────────
def load_partition(df_part: pd.DataFrame, yyyymm: int, retries: int = 4):
    """Append df_part to TABLE$yyyymm via gzip-CSV (no truncation)."""
    if df_part is None or df_part.empty:
        return
    df_part = df_part.reindex(columns=CSV_COLS)  # align to current schema; extra cols dropped
    fd, tmp = tempfile.mkstemp(suffix=".csv.gz"); _os.close(fd)
    df_part.to_csv(tmp, index=False, compression="gzip", date_format="%Y-%m-%d")

    dest = f"{table_ref}${yyyymm}"
    cfg = bigquery.LoadJobConfig(
        source_format=bigquery.SourceFormat.CSV,
        skip_leading_rows=1,
        write_disposition="WRITE_APPEND",
    )
    backoff = 5
    for attempt in range(1, retries + 1):
        try:
            with open(tmp, "rb") as buf:
                job = bq.load_table_from_file(buf, dest, job_config=cfg, rewind=True)
            tqdm.tqdm.write(f"⬆️  load {dest} rows {len(df_part)} (try {attempt})")
            job.result(timeout=300)
            tqdm.tqdm.write(f"✅ partition {yyyymm} rows {len(df_part)}")
            break
        except (gex.GoogleAPICallError, gex.RetryError, TimeoutError) as e:
            tqdm.tqdm.write(f"⚠️  {dest} {e} — backoff {backoff}s")
            time.sleep(backoff); backoff *= 2
    _os.remove(tmp)

# ───────────────────────── Checkpoint & helpers ─────────────────────
def read_checkpoint() -> Set[str]:
    return set(open(CHECKFILE).read().splitlines()) if _os.path.exists(CHECKFILE) else set()

def add_checkpoint(sym: str):
    with open(CHECKFILE, "a") as f:
        f.write(sym + "\n")

def add_failure(sym: str):
    with open(FAILFILE, "a") as f:
        f.write(sym + "\n")

def symbols_already_loaded() -> Set[str]:
    """Return distinct symbols already in BigQuery (used for gap-fill)."""
    q = f"SELECT DISTINCT symbol FROM `{table_ref}`"
    return {row.symbol for row in bq.query(q).result()}

def fallback_universe_from_bq() -> List[str]:
    """If AV listing fails/empty, derive a symbol universe from existing tables in BQ."""
    candidates: Set[str] = set()
    candidate_tables = [
        f"{PROJECT}.{DATASET}.daily_price",
        f"{PROJECT}.{DATASET}.balance_sheet_2",
        f"{PROJECT}.{DATASET}.income_statement_2",
        f"{PROJECT}.{DATASET}.cash_flow_2",
        f"{PROJECT}.{DATASET}.{TABLE}",
    ]
    for tbl in candidate_tables:
        try:
            rows = bq.query(f"SELECT DISTINCT symbol FROM `{tbl}`").result()
            for r in rows:
                if getattr(r, "symbol", None):
                    candidates.add(r.symbol)
        except gex.NotFound:
            continue
    return sorted(candidates)

# ───────────────────────── De-duplication helper ────────────────────
def dedupe_partitions(parts: Set[int]):
    """De-duplicate within each yyyymm partition (one row per (symbol, fiscalDateEnding))."""
    import tqdm as _tqdm
    if not parts:
        _tqdm.tqdm.write("🧹 dedupe: no partitions to process")
        return

    sql = f"""
    FOR part IN (SELECT p FROM UNNEST(@parts) AS p) DO
      CREATE OR REPLACE TEMP TABLE tmp AS
      SELECT * EXCEPT(rn) FROM (
        SELECT t.*,
               ROW_NUMBER() OVER (
                 PARTITION BY symbol, fiscalDateEnding
                 ORDER BY yyyymm DESC
               ) AS rn
        FROM `{table_ref}` AS t
        WHERE yyyymm = part.p         -- ✅ use part.p
      )
      WHERE rn = 1;

      DELETE FROM `{table_ref}` WHERE yyyymm = part.p;  -- ✅ use part.p
      INSERT INTO `{table_ref}` SELECT * FROM tmp;
    END FOR;
    """
    job = bq.query(
        sql,
        job_config=bigquery.QueryJobConfig(
            query_parameters=[bigquery.ArrayQueryParameter("parts", "INT64", sorted(parts))]
        ),
    )
    job.result()
    _tqdm.tqdm.write(f"🧹 dedupe: processed {len(parts)} partition(s)")


# ───────────────────────── Main async entrypoint ────────────────────
async def run(mode: str, refetch_on_schema_change: bool):
    if not API_KEY:
        raise SystemExit("❌  Set ALPHAVANTAGE_API_KEY and retry.")

    # Shared state
    sem                         = asyncio.Semaphore(CONCURRENCY)
    pending: Dict[int, List[pd.DataFrame]] = defaultdict(list)
    pending_rows: Dict[int, int]           = defaultdict(int)
    part_locks: Dict[int, asyncio.Lock]    = {}      # per-partition flush locks
    touched_parts: Set[int]                 = set()
    schema_changed_flag: bool               = schema_changed_initial

    async def maybe_flush(part: int):
        """Flush a partition buffer if it exceeds FLUSH_ROWS (with per-partition lock)."""
        lock = part_locks.setdefault(part, asyncio.Lock())
        async with lock:
            if pending_rows[part] >= FLUSH_ROWS:
                batch = pd.concat(pending[part]); pending[part].clear(); pending_rows[part] = 0
                await asyncio.to_thread(load_partition, batch, part)

    connector = aiohttp.TCPConnector(limit=CONCURRENCY)
    async with aiohttp.ClientSession(connector=connector, timeout=aiohttp.ClientTimeout(total=90)) as session:
        # Universe (fetch once, split by status)
        active, delisted = await listing_all(session)
        tqdm.tqdm.write(f"ℹ️  LISTING_STATUS counts → active: {len(active):,}, delisted: {len(delisted):,}")
        universe = sorted(set(active + delisted))

        if len(universe) == 0:
            fb = fallback_universe_from_bq()
            tqdm.tqdm.write(f"⚠️ Alpha Vantage LISTING_STATUS returned 0 symbols; using BQ fallback universe: {len(fb):,} symbols")
            universe = fb

        # Decide todo list (gap-fill = symbols not present in table)
        existing = symbols_already_loaded()
        if mode == "auto":
            mode = "full" if len(existing) == 0 else "gapfill"

        if mode == "full":
            todo = universe
            todo_desc = "FULL crawl (quarterly)"
        elif mode == "gapfill":
            todo = [s for s in universe if s not in existing]
            todo_desc = "GAP-FILL (missing symbols only, quarterly)"
        else:
            raise SystemExit(f"Unknown mode: {mode}")

        tqdm.tqdm.write(
            f"Mode: {todo_desc} | AV universe {len(universe):,} | "
            f"already in BQ {len(existing):,} | to fetch {len(todo):,}"
        )

        pbar = tqdm.tqdm(total=len(todo), desc="Symbols processed")

        async def worker(sym: str):
            nonlocal schema_changed_flag
            async with sem:
                df = await fetch_balance_sheet_quarterly(session, sym)
                if df is None or df.empty:
                    add_failure(sym)
                    pbar.update(1)
                    return

                # Mid-run schema evolve if needed
                new_cols = set(df.columns) - set(CSV_COLS)
                if new_cols:
                    changed = await ensure_columns_midrun(new_cols)
                    schema_changed_flag = schema_changed_flag or changed

                # Buffer per partition
                for part, grp in df.groupby("yyyymm"):
                    pending[part].append(grp)
                    pending_rows[part] += len(grp)
                    touched_parts.add(int(part))
                    await maybe_flush(part)

                # success-only checkpoint
                add_checkpoint(sym)
                pbar.update(1)

        tasks = [asyncio.create_task(worker(sym)) for sym in todo]
        await asyncio.gather(*tasks)
        pbar.close()

        # If schema changed and user asked to refetch, re-run already-loaded symbols this same run
        if schema_changed_flag and refetch_on_schema_change and mode != "full" and universe:
            tqdm.tqdm.write("🔁 Schema evolved mid-run → refetching already-loaded symbols to backfill new columns…")
            already = [s for s in universe if s in existing]
            pbar2 = tqdm.tqdm(total=len(already), desc="Refetch for new columns")
            async def worker_refill(sym: str):
                async with sem:
                    df = await fetch_balance_sheet_quarterly(session, sym)
                    if df is None or df.empty:
                        return
                    for part, grp in df.groupby("yyyymm"):
                        pending[part].append(grp)
                        pending_rows[part] += len(grp)
                        touched_parts.add(int(part))
                        await maybe_flush(part)
                    pbar2.update(1)
            await asyncio.gather(*(asyncio.create_task(worker_refill(s)) for s in already))
            pbar2.close()

    # Final flush
    for part, dfs in pending.items():
        if dfs:
            await asyncio.to_thread(load_partition, pd.concat(dfs), part)

    # End-of-run de-dup only for touched partitions
    await asyncio.to_thread(dedupe_partitions, touched_parts)

# ────────────────────────────────────────────────────────────────────
if __name__ == "__main__":
    # Jupyter/Colab-friendly: ignore unknown args like "-f <kernel.json>"
    parser = argparse.ArgumentParser()
    parser.add_argument("--mode", choices=["auto", "full", "gapfill"], default="auto",
                        help="auto=full if empty else gap-fill")
    parser.add_argument("--refetch-on-schema-change", action="store_true",
                        help="If schema evolves, refetch already-loaded symbols this run")
    args, _unknown = parser.parse_known_args()
    asyncio.run(run(args.mode, args.refetch_on_schema_change))


➡️  created table fluid-terminal-465516-s7.magic_formula.balance_sheet with 40 columns
ℹ️  LISTING_STATUS counts → active: 7,842, delisted: 0
Mode: FULL crawl (quarterly) | AV universe 7,842 | already in BQ 0 | to fetch 7,842


Symbols processed: 100%|██████████| 7842/7842 [1:43:33<00:00,  1.26it/s]


⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202107 rows 229 (try 1)
✅ partition 202107 rows 229
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202110 rows 234 (try 1)
✅ partition 202110 rows 234
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202201 rows 233 (try 1)
✅ partition 202201 rows 233
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202204 rows 241 (try 1)
✅ partition 202204 rows 241
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202207 rows 238 (try 1)
✅ partition 202207 rows 238
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202301 rows 235 (try 1)
✅ partition 202301 rows 235
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202304 rows 241 (try 1)
✅ partition 202304 rows 241
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202307 rows 237 (try 1)
✅ partition 202307 rows 237
⬆️  load fluid-terminal-465516-s7.magic_formula.balance_sheet$202310 rows 244 (try 1)
✅ 

In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
alpha_vantage_daily_price_auto.py  –  full-crawl OR gap-fill (auto) ✅

Behavior
--------
* If the destination table has **no symbols**, run a **full crawl** (all AV symbols).
* If the table already has data, run a **gap-fill** for **missing** symbols only.
* Safe + fast: async fetch, rate-limited, WRITE_APPEND, per-partition flush locks.
* End-of-run de-dup cleans only the partitions we touched.

Auth
----
* Works in Colab (user auth), with a service-account JSON via
  GOOGLE_APPLICATION_CREDENTIALS, or with gcloud ADC.

Env
---
* Alpha Vantage key via ALPHAVANTAGE_API_KEY (falls back to literal if unset).
"""

# ───────────────────────────── CONFIG ───────────────────────────────
PROJECT   = "fluid-terminal-465516-s7"      # GCP project ID
DATASET   = "magic_formula"                 # BigQuery dataset
TABLE     = "daily_price"                   # Destination table name
CHECKFILE = "av_done_symbols.txt"           # success-only (not used to skip in full mode)
FAILFILE  = "av_failed_symbols.txt"         # failures recorded here

import os as _os
API_KEY   = _os.getenv("ALPHAVANTAGE_API_KEY") or "IXNJPOSFX5OJYYQD"

CALLS_PER_MIN  = 75                         # paid-tier limit (free=5)
CONCURRENCY    = 50                         # concurrent HTTP requests
FLUSH_ROWS     = 100_000                    # per-partition flush threshold
PART_START, PART_END = 199901, 204001       # RANGE partition yyyymm

# ───────────────────────────── IMPORTS ──────────────────────────────
import io, csv, time, asyncio, tempfile, aiohttp, nest_asyncio, sys
from collections import defaultdict
from typing import Dict, List, Set
import pandas as pd
import tqdm
from aiolimiter import AsyncLimiter

from google.cloud import bigquery
from google.api_core import exceptions as gex
from google.auth.exceptions import DefaultCredentialsError, RefreshError
from google.oauth2 import service_account

nest_asyncio.apply()

# ───────────────────────── Auth-robust BigQuery client ──────────────
def get_bq_client() -> bigquery.Client:
    # 1) Colab / Notebook user auth
    try:
        from google.colab import auth as colab_auth  # type: ignore
        colab_auth.authenticate_user()
        return bigquery.Client(project=PROJECT)
    except Exception:
        pass

    # 2) Service account via GOOGLE_APPLICATION_CREDENTIALS
    sa_path = _os.getenv("GOOGLE_APPLICATION_CREDENTIALS")
    if sa_path and _os.path.exists(sa_path):
        creds = service_account.Credentials.from_service_account_file(sa_path)
        return bigquery.Client(project=PROJECT, credentials=creds)

    # 3) Application Default Credentials (gcloud)
    #    Make sure you've run:  gcloud auth application-default login
    try:
        return bigquery.Client(project=PROJECT)
    except (DefaultCredentialsError, RefreshError) as e:
        raise RuntimeError(
            "No Google Cloud credentials found. Do one of:\n"
            "  • In Colab: from google.colab import auth; auth.authenticate_user()\n"
            "  • With service account: set GOOGLE_APPLICATION_CREDENTIALS to your JSON path\n"
            "  • With gcloud: run `gcloud auth application-default login`"
        ) from e

bq = get_bq_client()

# ───────────────────── Alpha Vantage async fetchers ─────────────────
BASE_URL     = "https://www.alphavantage.co/query"
RATE_LIMITER = AsyncLimiter(CALLS_PER_MIN, 60)

async def fetch_series(session: aiohttp.ClientSession, sym: str) -> pd.DataFrame | None:
    """Fetch TIME_SERIES_DAILY_ADJUSTED for a symbol; return tidy DataFrame or None."""
    params = {
        "function": "TIME_SERIES_DAILY_ADJUSTED",
        "symbol": sym,
        "outputsize": "full",
        "apikey": API_KEY,
    }
    async with RATE_LIMITER:
        try:
            async with session.get(BASE_URL, params=params, timeout=45) as resp:
                if resp.status != 200:
                    return None
                data = await resp.json(content_type=None)
        except (aiohttp.ClientError, asyncio.TimeoutError):
            return None

    key = next((k for k in data if "Time Series" in k), None)
    if not key or not data.get(key):
        return None

    df = (
        pd.DataFrame.from_dict(data[key], orient="index")
          .reset_index()
          .rename(columns={
              "index": "date",
              "1. open": "open",
              "2. high": "high",
              "3. low": "low",
              "4. close": "close",
              "5. adjusted close": "adj_close",
              "6. volume": "volume",
              "7. dividend amount": "dividend",
              "8. split coefficient": "split_coef",
          })
    )
    df["symbol"] = sym
    df["date"]   = pd.to_datetime(df["date"]).dt.date
    df["yyyymm"] = df["date"].apply(lambda d: d.year * 100 + d.month).astype("int64")

    float_cols = ["open","high","low","close","adj_close","dividend","split_coef"]
    df[float_cols] = df[float_cols].apply(pd.to_numeric, errors="coerce")
    df["volume"]   = pd.to_numeric(df["volume"], errors="coerce").astype("Int64")
    return df

async def listing(session: aiohttp.ClientSession, state: str) -> List[str]:
    """Async, rate-limited Alpha Vantage LISTING_STATUS CSV → list of stock symbols."""
    params = {
        "function": "LISTING_STATUS",
        "state": state,           # "active" or "delisted"
        "datatype": "csv",
        "apikey": API_KEY,
    }
    async with RATE_LIMITER:
        try:
            async with session.get(BASE_URL, params=params, timeout=45) as resp:
                if resp.status != 200:
                    tqdm.tqdm.write(f"⚠️ listing {state} http {resp.status}")
                    return []
                txt = await resp.text()
        except (aiohttp.ClientError, asyncio.TimeoutError):
            tqdm.tqdm.write(f"⚠️ listing {state} fetch error")
            return []
    rdr = csv.DictReader(io.StringIO(txt))
    return [r["symbol"] for r in rdr if r.get("assetType") == "Stock" and r.get("symbol")]

# ───────────────────────── BigQuery bootstrapping ───────────────────
# Dataset
try:
    bq.get_dataset(f"{PROJECT}.{DATASET}")
except gex.NotFound:
    bq.create_dataset(bigquery.Dataset(f"{PROJECT}.{DATASET}"))

# Table (partitioned & clustered)
table_ref = f"{PROJECT}.{DATASET}.{TABLE}"
if not any(t.table_id == TABLE for t in bq.list_tables(f"{PROJECT}.{DATASET}")):
    schema = [
        bigquery.SchemaField("symbol", "STRING"),
        bigquery.SchemaField("date", "DATE"),
        bigquery.SchemaField("open", "FLOAT"),
        bigquery.SchemaField("high", "FLOAT"),
        bigquery.SchemaField("low", "FLOAT"),
        bigquery.SchemaField("close", "FLOAT"),
        bigquery.SchemaField("adj_close", "FLOAT"),
        bigquery.SchemaField("volume", "INT64"),
        bigquery.SchemaField("dividend", "FLOAT"),
        bigquery.SchemaField("split_coef", "FLOAT"),
        bigquery.SchemaField("yyyymm", "INT64"),
    ]
    tbl = bigquery.Table(table_ref, schema=schema)
    tbl.range_partitioning = bigquery.RangePartitioning(
        field="yyyymm",
        range_=bigquery.PartitionRange(PART_START, PART_END, 1),
    )
    tbl.clustering_fields = ["symbol"]
    bq.create_table(tbl)
    tqdm.tqdm.write(f"➡️  created table {table_ref}")

# Ensure we can read schema (for CSV order if needed)
tbl = bq.get_table(table_ref)

# ───────────────────────── Load to a single partition ───────────────
CSV_COLS = [
    "symbol", "date", "open", "high", "low", "close",
    "adj_close", "volume", "dividend", "split_coef", "yyyymm",
]

def load_partition(df_part: pd.DataFrame, yyyymm: int, retries: int = 3):
    """Append df_part to TABLE$yyyymm via gzip-CSV (no truncation)."""
    if df_part is None or df_part.empty:
        return
    df_part = df_part[CSV_COLS]
    fd, tmp = tempfile.mkstemp(suffix=".csv.gz"); _os.close(fd)
    df_part.to_csv(tmp, index=False, compression="gzip", date_format="%Y-%m-%d")

    dest = f"{table_ref}${yyyymm}"
    cfg = bigquery.LoadJobConfig(
        source_format=bigquery.SourceFormat.CSV,
        skip_leading_rows=1,
        write_disposition="WRITE_APPEND",
    )
    for attempt in range(1, retries + 1):
        try:
            with open(tmp, "rb") as buf:
                job = bq.load_table_from_file(buf, dest, job_config=cfg, rewind=True)
            tqdm.tqdm.write(f"⬆️  load {dest} rows {len(df_part)} (try {attempt})")
            job.result(timeout=300)
            tqdm.tqdm.write(f"✅ partition {yyyymm} rows {len(df_part)}")
            break
        except (gex.GoogleAPICallError, gex.RetryError, TimeoutError) as e:
            tqdm.tqdm.write(f"⚠️  {dest} {e} (try {attempt})")
            time.sleep(10)
    _os.remove(tmp)

# ───────────────────────── Checkpoint & helpers ─────────────────────
def read_checkpoint() -> Set[str]:
    return set(open(CHECKFILE).read().splitlines()) if _os.path.exists(CHECKFILE) else set()

def add_checkpoint(sym: str):
    with open(CHECKFILE, "a") as f:
        f.write(sym + "\n")

def add_failure(sym: str):
    with open(FAILFILE, "a") as f:
        f.write(sym + "\n")

def symbols_already_loaded() -> Set[str]:
    """Return distinct symbols already in BigQuery (used for gap-fill)."""
    q = f"SELECT DISTINCT symbol FROM `{table_ref}`"
    return {row.symbol for row in bq.query(q).result()}

# ───────────────────────── De-duplication helper ────────────────────
def dedupe_partitions(parts: Set[int]):
    """De-duplicate rows within each provided yyyymm partition (one row per (symbol, date))."""
    import tqdm as _tqdm
    if not parts:
        _tqdm.tqdm.write("🧹 dedupe: no partitions to process")
        return

    sql = f"""
    -- De-duplicate within each requested partition (yyyymm).
    FOR part IN (SELECT p FROM UNNEST(@parts) AS p) DO
      CREATE OR REPLACE TEMP TABLE tmp AS
      SELECT symbol, date, open, high, low, close, adj_close, volume, dividend, split_coef, yyyymm
      FROM (
        SELECT t.*,
               ROW_NUMBER() OVER (PARTITION BY symbol, date ORDER BY yyyymm DESC) AS rn
        FROM `{table_ref}` AS t
        WHERE yyyymm = part
      )
      WHERE rn = 1;

      DELETE FROM `{table_ref}` WHERE yyyymm = part;

      INSERT INTO `{table_ref}` (
        symbol, date, open, high, low, close, adj_close, volume, dividend, split_coef, yyyymm
      )
      SELECT * FROM tmp;
    END FOR;
    """
    job = bq.query(
        sql,
        job_config=bigquery.QueryJobConfig(
            query_parameters=[bigquery.ArrayQueryParameter("parts", "INT64", sorted(parts))]
        ),
    )
    job.result()
    _tqdm.tqdm.write(f"🧹 dedupe: processed {len(parts)} partition(s)")

# ───────────────────────── Main async entrypoint ────────────────────
async def main():
    # Shared state
    sem                         = asyncio.Semaphore(CONCURRENCY)
    pending: Dict[int, List[pd.DataFrame]] = defaultdict(list)
    pending_rows: Dict[int, int]           = defaultdict(int)
    part_locks: Dict[int, asyncio.Lock]    = {}      # per-partition flush locks
    touched_parts: Set[int]                 = set()

    async def maybe_flush(part: int):
        """Flush a partition buffer if it exceeds FLUSH_ROWS (with per-partition lock)."""
        lock = part_locks.setdefault(part, asyncio.Lock())
        async with lock:
            if pending_rows[part] >= FLUSH_ROWS:
                batch = pd.concat(pending[part]); pending[part].clear(); pending_rows[part] = 0
                await asyncio.to_thread(load_partition, batch, part)

    # Single global session (listings + series)
    connector = aiohttp.TCPConnector(limit=CONCURRENCY)
    async with aiohttp.ClientSession(connector=connector, timeout=aiohttp.ClientTimeout(total=90)) as session:
        # Build AV universe
        active, delisted = await asyncio.gather(
            listing(session, "active"),
            listing(session, "delisted")
        )
        universe = sorted(set(active + delisted))

        # Decide mode
        existing = symbols_already_loaded()   # set of symbols in BQ
        if len(existing) == 0:
            mode = "full"
            # Full crawl: ignore local checkpoint when building todo to guarantee a truly full refill
            todo = universe
        else:
            mode = "gapfill"
            # Gap fill: rely on BQ to skip already-loaded symbols; ignore checkpoint here
            todo = [s for s in universe if s not in existing]

        tqdm.tqdm.write(
            f"Mode: {mode.upper()} | AV universe {len(universe):,} | "
            f"already in BQ {len(existing):,} | to fetch {len(todo):,}"
        )

        # Workers
        pbar = tqdm.tqdm(total=len(todo), desc="Symbols processed")
        async def worker(sym: str):
            async with sem:
                df = await fetch_series(session, sym)
                if df is not None and not df.empty:
                    for part, grp in df.groupby("yyyymm"):
                        pending[part].append(grp)
                        pending_rows[part] += len(grp)
                        touched_parts.add(int(part))
                        await maybe_flush(part)
                    # Record success; ignored for building gap-fill todo but useful for audits
                    add_checkpoint(sym)
                else:
                    add_failure(sym)
                pbar.update(1)

        tasks = [asyncio.create_task(worker(sym)) for sym in todo]
        await asyncio.gather(*tasks)
        pbar.close()

    # Final flush for any leftover partitions
    for part, dfs in pending.items():
        if dfs:
            await asyncio.to_thread(load_partition, pd.concat(dfs), part)

    # End-of-run de-dup only for touched partitions
    await asyncio.to_thread(dedupe_partitions, touched_parts)

# ────────────────────────────────────────────────────────────────────
if __name__ == "__main__":
    asyncio.run(main())


Mode: GAPFILL | AV universe 14,803 | already in BQ 15,014 | to fetch 255


Symbols processed: 100%|██████████| 255/255 [02:24<00:00,  1.77it/s]


⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$202511 rows 825 (try 1)
✅ partition 202511 rows 825
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$202512 rows 858 (try 1)
✅ partition 202512 rows 858
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201506 rows 181 (try 1)
✅ partition 201506 rows 181
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201507 rows 198 (try 1)
✅ partition 201507 rows 198
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201508 rows 189 (try 1)
✅ partition 201508 rows 189
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201509 rows 176 (try 1)
✅ partition 201509 rows 176
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201510 rows 176 (try 1)
✅ partition 201510 rows 176
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201511 rows 160 (try 1)
✅ partition 201511 rows 160
⬆️  load fluid-terminal-465516-s7.magic_formula.daily_price$201512 rows 176 (try 1)
✅ partition 201512 r

BadRequest: 400 GET https://bigquery.googleapis.com/bigquery/v2/projects/fluid-terminal-465516-s7/queries/c7e8cd47-dc7a-4316-bfe6-5955a8fc3bc1?maxResults=0&location=US&prettyPrint=false: Query error: No matching signature for operator = for argument types: INT64, STRUCT<p INT64>
  Signature: T1 = T1
    Unable to find common supertype for templated argument <T1>
      Input types for <T1>: {INT64, STRUCT<p INT64>} at [7:15] at [4:7]

Location: US
Job ID: c7e8cd47-dc7a-4316-bfe6-5955a8fc3bc1
